In [2]:
import numpy as np
import scipy as sp
#import gridData as gd
import pandas as pd
import matplotlib
from matplotlib import pyplot as plt
import seaborn as sns
#import pytraj as pt
import py3Dmol as pmol

import sys
import os
import tqdm
import gc
import copy

from collections import defaultdict
import itertools


import plotly as ply
ply.io.renderers.default="notebook"

import ipywidgets as widgets
from ipywidgets import interact

import sklearn as skl
from sklearn.decomposition import PCA
from sklearn.cluster import OPTICS, cluster_optics_dbscan

## Testing py3Dmol for molecule viewing

In [2]:
p = pmol.view(query='pdb:1ycr')
p.setStyle({'cartoon': {'color':'spectrum'}})
p.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## testing plotly for interactive 3D rendering

In [13]:
#Toy test system to test rendering of 3d scatter plots with plotly
pointsList=np.array([
    np.array([0.,0.,10.])+np.random.random(3),
    np.array([0.,0.,-10.])+np.random.random(3),
    np.array([1.,0.,0.])*5.+np.random.random(3),
    np.array([np.cos(120.*np.pi/180.),np.sin(120.*np.pi/180.),0])*5.+np.random.random(3),
    np.array([np.cos(-120*np.pi/180.),np.sin(-120.*np.pi/180.),0])*5.+np.random.random(3)
])
pointsFrame=pd.DataFrame(
    {'X':pointsList[:,0],
     'Y':pointsList[:,1],
     'Z':pointsList[:,2]})
pointsFrame

X         Y          Z
0  0.324507  0.018762  10.064975
1  0.511473  0.171533  -9.802700
2  5.025049  0.497257   0.569166
3 -1.554803  5.141253   0.080946
4 -2.376186 -3.565475   0.697159

In [14]:
import plotly as ply

In [15]:
ply.io.renderers.default="notebook"

In [16]:
go=ply.graph_objs
fig=go.Figure(data=[go.Scatter3d(x=pointsFrame['X'],y=pointsFrame['Y'],z=pointsFrame['Z'],
                                mode='markers')])
fig.show()

# Load Coordinate data sets

In [7]:
dataDir="simulationData"

potFilePattern="pot_"
potDataFiles=[fileName for fileName in os.listdir(dataDir) \
              if potFilePattern in fileName]
print("potassium data file list:",potDataFiles)

print()
alphaFilePattern="atomCA_"
alphaDataFiles=[fileName for fileName in os.listdir(dataDir) \
                if alphaFilePattern in fileName] 
print("alpha carbon control atom data file list:",alphaDataFiles)

potassium data file list: ['pot_165552.dat', 'pot_165627.dat', 'pot_165623.dat', 'pot_165554.dat', 'pot_165581.dat', 'pot_165557.dat', 'pot_165530.dat', 'pot_165872.dat', 'pot_165711.dat', 'pot_165891.dat', 'pot_166052.dat', 'pot_165570.dat', 'pot_166069.dat', 'pot_166136.dat', 'pot_166095.dat', 'pot_165774.dat']

alpha carbon control atom data file list: ['atomCA_resid2377.dat', 'atomCA_resid1178.dat', 'atomCA_resid3796.dat', 'atomCA_resid958.dat', 'atomCA_resid1366.dat']


In [9]:
atomDataFrames=[]
for potFile in tqdm.tqdm_notebook(potDataFiles,desc='Loading Potassium Data'):
    potID=potFile.split('.')[0].split('_')[-1]
    potFilePath='/'.join([dataDir,potFile])
    tempFrame=pd.read_csv(potFilePath,delim_whitespace=True,skiprows=1,
                          names=['Frame','X','Y','Z','Unused1','Unused2','Unused3'])
    tempFrame=tempFrame.drop(columns=[colName for colName in tempFrame.columns \
                                      if 'Unused' in colName])
    tempFrame['AtomID']=potID
    tempFrame['AtomType']='POT'
    tempFrame=tempFrame[['AtomID','AtomType','Frame','X','Y','Z']]
    atomDataFrames.append(tempFrame.copy())
    
for alphaFile in tqdm.tqdm_notebook(alphaDataFiles,'Loading Alpha Carbon Data'):
    alphaID=alphaFile.split('.')[0].split('_')[-1].replace('resid','')
    alphaFilePath='/'.join([dataDir,alphaFile])
    tempFrame=pd.read_csv(alphaFilePath,delim_whitespace=True,skiprows=1,
                          names=['Frame','X','Y','Z','Unused1','Unused2','Unused3'])
    tempFrame=tempFrame.drop(columns=[colName for colName in tempFrame.columns \
                                      if 'Unused' in colName])
    tempFrame['AtomID']=alphaID
    tempFrame['AtomType']='CA'
    tempFrame=tempFrame[['AtomID','AtomType','Frame','X','Y','Z']]
    atomDataFrames.append(tempFrame.copy())
    
atomDataFrame=pd.concat(atomDataFrames)
atomDataFrames=[]
del(atomDataFrames)
atomDataFrame.head()

AtomID AtomType  Frame         X         Y        Z
0  165552      POT      1  109.3891   81.3629  25.0487
1  165552      POT      2  105.4785  241.4059  92.7848
2  165552      POT      3  106.9650  240.9525  91.4489
3  165552      POT      4  106.4484  240.0916  91.4920
4  165552      POT      5  105.1581  240.6961  91.8088

In [10]:
atomDataFrame.AtomType.unique()

array(['POT', 'CA'], dtype=object)

In [11]:
atomDataFrame.to_csv('/'.join([dataDir,'atom_coordinate_data_table.csv']),
                     index=False)

## Visualize Loaded Atom Data as 3D scatter plot

In [12]:
atomDataFrame=pd.read_csv('/'.join([dataDir,'atom_coordinate_data_table.csv']))
atomDataFrame.head()

AtomID AtomType  Frame         X         Y        Z
0  165552      POT      1  109.3891   81.3629  25.0487
1  165552      POT      2  105.4785  241.4059  92.7848
2  165552      POT      3  106.9650  240.9525  91.4489
3  165552      POT      4  106.4484  240.0916  91.4920
4  165552      POT      5  105.1581  240.6961  91.8088

In [13]:
go=ply.graph_objs
fig=go.Figure(
    data=[
            go.Scatter3d(x=atomDataFrame.query('AtomType == "POT"')['X'],
                         y=atomDataFrame.query('AtomType == "POT"')['Y'],
                         z=atomDataFrame.query('AtomType == "POT"')['Z'],
                         mode='markers',
                         marker=dict(size=2,
                                     color='blue',
                                     colorscale='Viridis',
                                     opacity=.125)),
            go.Scatter3d(x=atomDataFrame.query('AtomType == "CA"')['X'],
                         y=atomDataFrame.query('AtomType == "CA"')['Y'],
                         z=atomDataFrame.query('AtomType == "CA"')['Z'],
                         mode='markers',
                         marker=dict(size=12,color='red',opacity=.75))
         ],
    layout=dict(width=800,height=600)
)
fig.show()

# Compute Potassium to Alpha Carbon Distances

In [14]:
tempFrames=[]
baseFrame=atomDataFrame.set_index('Frame')
for groupName,groupData in \
    tqdm.tqdm_notebook(atomDataFrame.query('AtomType == "CA"').groupby('AtomID'),
                       desc='Computing Distances'):
    tempFrame=baseFrame.join(groupData.set_index('Frame')[['X','Y','Z']],
                             rsuffix='_ref',how='outer')
    tempFrame['RefAtomID']=groupName
    tempFrame['Distance']=tempFrame[['X','Y','Z','X_ref','Y_ref','Z_ref']].apply(
        lambda x: np.sqrt(np.sum(
            [(x[0]-x[3])**2,
             (x[1]-x[4])**2,
             (x[2]-x[5])**2])),
        axis=1)
    tempFrames.append(tempFrame.copy())

diffData=pd.concat(tempFrames)
tempFrames=[]
del(tempFrames)
gc.collect()
diffData.head()

AtomID AtomType         X         Y         Z     X_ref    Y_ref  \
Frame                                                                     
1      165552      POT  109.3891   81.3629   25.0487  123.2928  110.994   
1      165627      POT   32.3418  165.3300   37.5258  123.2928  110.994   
1      165623      POT  187.0743   90.5251  102.1417  123.2928  110.994   
1      165554      POT   42.9653   78.8911   51.0144  123.2928  110.994   
1      165581      POT   57.8748  122.7727  107.9835  123.2928  110.994   

         Z_ref  RefAtomID    Distance  
Frame                                  
1      58.3107        958   46.665572  
1      58.3107        958  107.965260  
1      58.3107        958   80.051310  
1      58.3107        958   86.812093  
1      58.3107        958   82.979754

In [15]:
diffCoords=diffData.drop(
        columns=[colName for colName in diffData.columns if 'ref' in colName]
    ).reset_index().pivot_table(index=['Frame','AtomID','AtomType','X','Y','Z'],
                                columns='RefAtomID',values='Distance')
diffCoords.columns=np.array(diffCoords.columns.map(lambda x: 'D_%g'%(x)))
diffCoords=diffCoords.reset_index()
diffCoords.head()

Frame  AtomID AtomType         X         Y         Z      D_958     D_1178  \
0      1     958       CA  123.2928  110.9940   58.3107   0.000000  92.177611   
1      1    1178       CA   76.6708  159.4728  121.3417  92.177611   0.000000   
2      1    1366       CA   95.1964  126.0866   32.3294  41.136629  96.855696   
3      1    2377       CA   53.3092  115.8309   59.7553  70.165424  79.014331   
4      1    3796       CA  103.7853  171.4280   55.4642  63.568180  72.235503   

      D_1366     D_2377     D_3796  
0  41.136629  70.165424  63.568180  
1  96.855696  79.014331  72.235503  
2   0.000000  51.106721  51.621998  
3  51.106721   0.000000  75.214944  
4  51.621998  75.214944   0.000000

In [16]:
diffCoords.to_csv('/'.join([dataDir,'potassium_distance_data.csv']),
                  index=False)

# Visualize Potassium to Alpha Carbon Distances

We will use an ipython widget to allow the user to select which alpha carbon to use for colormapping the
potassium to alpha carbon distances.

In [149]:
diffCoords=pd.read_csv('/'.join([dataDir,'potassium_distance_data.csv']))
diffCoords.head()

Frame  AtomID AtomType         X         Y         Z      D_958     D_1178  \
0      1     958       CA  123.2928  110.9940   58.3107   0.000000  92.177611   
1      1    1178       CA   76.6708  159.4728  121.3417  92.177611   0.000000   
2      1    1366       CA   95.1964  126.0866   32.3294  41.136629  96.855696   
3      1    2377       CA   53.3092  115.8309   59.7553  70.165424  79.014331   
4      1    3796       CA  103.7853  171.4280   55.4642  63.568180  72.235503   

      D_1366     D_2377     D_3796  
0  41.136629  70.165424  63.568180  
1  96.855696  79.014331  72.235503  
2   0.000000  51.106721  51.621998  
3  51.106721   0.000000  75.214944  
4  51.621998  75.214944   0.000000

In [18]:
diffCoords.sort_values(['AtomID','Frame']).tail()

Frame  AtomID AtomType        X         Y        Z       D_958  \
43616   2077  166136      POT  80.8816  223.3779  20.3468  127.960128   
43637   2078  166136      POT  88.1827  216.8769  20.8253  119.425785   
43658   2079  166136      POT  85.9101  213.5211  22.8924  116.520063   
43679   2080  166136      POT  87.5495  208.5846  24.3888  110.868936   
43700   2081  166136      POT  91.2438  200.8141  23.9601  103.452520   

           D_1178     D_1366      D_2377     D_3796  
43616  112.182235  96.202377  112.633095  62.610885  
43637  108.561632  88.875757  108.786181  54.407042  
43658  105.470168  85.208274  104.386001  51.314128  
43679  102.451812  80.666047   99.734712  47.000275  
43700   99.975768  72.538005   94.789927  40.659838

In [19]:
import ipywidgets as widgets
from ipywidgets import interact

In [20]:
@interact
def color_by_distance(distanceColumn=[colName for colName in diffCoords.columns \
                                      if 'D_' in colName]):
    go=ply.graph_objs
    fig=go.Figure(
        data=[
                go.Scatter3d(x=diffCoords.query('AtomType == "POT"')['X'],
                             y=diffCoords.query('AtomType == "POT"')['Y'],
                             z=diffCoords.query('AtomType == "POT"')['Z'],
                             mode='markers',
                             marker=dict(size=2,
                                         color=diffCoords.query(
                                                 'AtomType == "POT"'
                                             )[distanceColumn],
                                         colorscale='RdBu',
                                         opacity=.125)),
                go.Scatter3d(
                    x=diffCoords.query(
                            '(AtomType == "CA") and (AtomID != %s)'%(distanceColumn.split('_')[-1])
                        )['X'],
                    y=diffCoords.query(
                            '(AtomType == "CA") and (AtomID != %s)'%(distanceColumn.split('_')[-1])
                        )['Y'],
                    z=diffCoords.query(
                            '(AtomType == "CA") and (AtomID != %s)'%(distanceColumn.split('_')[-1])
                        )['Z'],
                    mode='markers',
                    marker=dict(size=12,
                                color='black',
                                opacity=.25)),
                go.Scatter3d(x=diffCoords.query('AtomID == %s'%(distanceColumn.split('_')[-1]))['X'],
                             y=diffCoords.query('AtomID == %s'%(distanceColumn.split('_')[-1]))['Y'],
                             z=diffCoords.query('AtomID == %s'%(distanceColumn.split('_')[-1]))['Z'],
                             mode='markers',
                             marker=dict(size=12,color='red',opacity=.75))
             ],
        layout=dict(width=800,height=600)
    )
    fig.show()

interactive(children=(Dropdown(description='distanceColumn', options=('D_958', 'D_1178', 'D_1366', 'D_2377', '…

# Compute PCA projection

In [21]:
import sklearn as skl
from sklearn.decomposition import PCA

In [22]:
Xdata=diffCoords.query('AtomType == "POT"')[diffCoords.columns[-5:]]
Xdata.head()

D_958      D_1178      D_1366      D_2377      D_3796
5  132.703255  158.736050  161.974605  148.917295  185.519797
6   46.665572  128.234104   47.483162   74.414691   95.227241
7   86.812093  112.140092   72.832906   39.343976  110.823964
8   85.844916   99.317973   92.829412   60.282709  120.622686
9   64.929022  102.972238   24.265077   47.409354   58.214160

In [23]:
pca=PCA()

pca.fit(Xdata)

pca_coords=pca.transform(diffCoords[diffCoords.columns[-5:]])
pca_coords[:10]

array([[ -92.36958027,  -43.23515844,  -20.98241854,  -39.53352024,
          -8.62474089],
       [ -61.67236156,   80.78070756,   34.81190576,  -24.19951003,
          15.48067544],
       [-109.6038469 ,  -46.11865923,  -16.529022  ,   14.96258879,
          16.22040298],
       ...,
       [ -26.22338032,  -30.64675317,   42.40147382,   20.22039947,
          -7.77121906],
       [  -8.09234265,  -12.6624656 ,   41.36420923,   -0.71243343,
          -4.90427829],
       [ -84.66814926,  -33.20334896,   -3.63380097,   27.72520521,
           4.74670254]])

In [24]:
pcaData=diffCoords.join(
    pd.DataFrame(pca_coords,
                 columns=['PCA_%g'%ii for ii in np.arange(pca_coords.shape[1])]))
pcaData.head()

Frame  AtomID AtomType         X         Y         Z      D_958     D_1178  \
0      1     958       CA  123.2928  110.9940   58.3107   0.000000  92.177611   
1      1    1178       CA   76.6708  159.4728  121.3417  92.177611   0.000000   
2      1    1366       CA   95.1964  126.0866   32.3294  41.136629  96.855696   
3      1    2377       CA   53.3092  115.8309   59.7553  70.165424  79.014331   
4      1    3796       CA  103.7853  171.4280   55.4642  63.568180  72.235503   

      D_1366     D_2377     D_3796       PCA_0      PCA_1      PCA_2  \
0  41.136629  70.165424  63.568180  -92.369580 -43.235158 -20.982419   
1  96.855696  79.014331  72.235503  -61.672362  80.780708  34.811906   
2   0.000000  51.106721  51.621998 -109.603847 -46.118659 -16.529022   
3  51.106721   0.000000  75.214944  -92.192533 -20.807768  52.877672   
4  51.621998  75.214944   0.000000 -101.597084  25.930154 -42.318357   

       PCA_3      PCA_4  
0 -39.533520  -8.624741  
1 -24.199510  15.480675  
2  14.962589  16.220403  
3  25.542441 -16.465812  
4  17.236239 -16.867316

In [25]:
pcaData.to_csv('/'.join([dataDir,'pca_projection_data.csv']),
                  index=False)

# Visualize PCA projection data

Lets see how well the first 3 principal components do at reconstructing our data set.

In [198]:
import ipywidgets as widgets
from ipywidgets import interact_manual

In [27]:
pcaData=pd.read_csv('/'.join([dataDir,'pca_projection_data.csv']))
pcaData.head()

Frame  AtomID AtomType         X         Y         Z      D_958     D_1178  \
0      1     958       CA  123.2928  110.9940   58.3107   0.000000  92.177611   
1      1    1178       CA   76.6708  159.4728  121.3417  92.177611   0.000000   
2      1    1366       CA   95.1964  126.0866   32.3294  41.136629  96.855696   
3      1    2377       CA   53.3092  115.8309   59.7553  70.165424  79.014331   
4      1    3796       CA  103.7853  171.4280   55.4642  63.568180  72.235503   

      D_1366     D_2377     D_3796       PCA_0      PCA_1      PCA_2  \
0  41.136629  70.165424  63.568180  -92.369580 -43.235158 -20.982419   
1  96.855696  79.014331  72.235503  -61.672362  80.780708  34.811906   
2   0.000000  51.106721  51.621998 -109.603847 -46.118659 -16.529022   
3  51.106721   0.000000  75.214944  -92.192533 -20.807768  52.877672   
4  51.621998  75.214944   0.000000 -101.597084  25.930154 -42.318357   

       PCA_3      PCA_4  
0 -39.533520  -8.624741  
1 -24.199510  15.480675  
2  14.962589  16.220403  
3  25.542441 -16.465812  
4  17.236239 -16.867316

In [28]:
@interact_manual
def color_by_distance(colorColumn=widgets.Dropdown(
                          options=[colName for colName in pcaData.columns \
                                   if ('PCA_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='D_958'),
                      xCol=widgets.Dropdown(
                          options=[colName for colName in pcaData.columns \
                                   if ('PCA_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='PCA_0'),
                      yCol=widgets.Dropdown(
                          options=[colName for colName in pcaData.columns \
                                   if ('PCA_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='PCA_1'),
                      zCol=widgets.Dropdown(
                          options=[colName for colName in pcaData.columns \
                                   if ('PCA_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='PCA_2'),
                     ):
    go=ply.graph_objs
    fig=go.Figure(
        data=[
                go.Scatter3d(x=pcaData.query('AtomType == "POT"')[xCol],
                             y=pcaData.query('AtomType == "POT"')[yCol],
                             z=pcaData.query('AtomType == "POT"')[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color=pcaData.query(
                                                 'AtomType == "POT"'
                                             )[colorColumn],
                                         colorscale='RdBu',
                                         opacity=.125)),
                go.Scatter3d(
                    x=pcaData.query(
                            '(AtomType == "CA")'
                        )[xCol],
                    y=pcaData.query(
                            '(AtomType == "CA")'
                        )[yCol],
                    z=pcaData.query(
                            '(AtomType == "CA")'
                        )[zCol],
                    mode='markers',
                    marker=dict(size=12,
                                color='black',
                                opacity=.25))
             ],
        layout=dict(
            width=800,height=600)
    )
    fig.show()

interactive(children=(Dropdown(description='colorColumn', index=3, options=('X', 'Y', 'Z', 'D_958', 'D_1178', …

In [29]:
@interact_manual
def testingFun( #'D_958', 'D_1178', 'D_1366', 'D_2377', 'D_3796'
    X_bound=widgets.FloatRangeSlider(     min=pcaData.X.min(),max=pcaData.X.max(),
                                   value=(pcaData.X.min(),pcaData.X.max())),
    
    Y_bound=widgets.FloatRangeSlider(     min=pcaData.Y.min(),max=pcaData.Y.max(),
                                   value=(pcaData.Y.min(),pcaData.Y.max())),
    
    Z_bound=widgets.FloatRangeSlider(     min=pcaData.Z.min(),max=pcaData.Z.max(),
                                   value=(pcaData.Z.min(),pcaData.Z.max())),
    
    D_958_bound=widgets.FloatRangeSlider( min=pcaData.D_958.min(),max=pcaData.D_958.max(),
                                   value=(pcaData.D_958.min(),pcaData.D_958.max())),
    
    D_1178_bound=widgets.FloatRangeSlider(min=pcaData.D_1178.min(),max=pcaData.D_1178.max(),
                                   value=(pcaData.D_1178.min(),pcaData.D_1178.max())),
    
    D_1366_bound=widgets.FloatRangeSlider(min=pcaData.D_1366.min(),max=pcaData.D_1366.max(),
                                   value=(pcaData.D_1366.min(),pcaData.D_1366.max())),
    
    D_2377_bound=widgets.FloatRangeSlider(min=pcaData.D_2377.min(),max=pcaData.D_2377.max(),
                                   value=(pcaData.D_2377.min(),pcaData.D_2377.max())),
    
    D_3796_bound=widgets.FloatRangeSlider(min=pcaData.D_3796.min(),max=pcaData.D_3796.max(),
                                   value=(pcaData.D_3796.min(),pcaData.D_3796.max())),
    
    PCA_0_bound=widgets.FloatRangeSlider( min=pcaData.PCA_0.min(),max=pcaData.PCA_0.max(),
                                   value=(pcaData.PCA_0.min(),pcaData.PCA_0.max())),
    
    PCA_1_bound=widgets.FloatRangeSlider( min=pcaData.PCA_1.min(),max=pcaData.PCA_1.max(),
                                   value=(pcaData.PCA_1.min(),pcaData.PCA_1.max())),
    
    PCA_2_bound=widgets.FloatRangeSlider( min=pcaData.PCA_1.min(),max=pcaData.PCA_1.max(),
                                   value=(pcaData.PCA_1.min(),pcaData.PCA_1.max())),
    
    PCA_3_bound=widgets.FloatRangeSlider( min=pcaData.PCA_3.min(),max=pcaData.PCA_3.max(),
                                   value=(pcaData.PCA_3.min(),pcaData.PCA_3.max())),
    
    PCA_4_bound=widgets.FloatRangeSlider( min=pcaData.PCA_4.min(),max=pcaData.PCA_4.max(),
                                   value=(pcaData.PCA_4.min(),pcaData.PCA_4.max())),
    xCol=widgets.Dropdown(options=pcaData.columns[3:],value='X'),
    yCol=widgets.Dropdown(options=pcaData.columns[3:],value='Y'),
    zCol=widgets.Dropdown(options=pcaData.columns[3:],value='Z'),
    ):
    kwargDict=dict(locals())
    print(kwargDict.keys(),kwargDict.values())
    kwargDict=dict(locals())
    kwargKeys=np.array(list(kwargDict.keys()))[:13]
    for kwargKey in kwargKeys:
        print(kwargKey,end="")
        print(len(kwargDict[kwargKey]),kwargDict[kwargKey][0],kwargDict[kwargKey][1])
    queryStr=' and '.join(
        ['({factorKey:s} > {factorMin:f}) and ({factorKey:s} < {factorMax:f})'.format(
            factorKey='_'.join(kwargKey.split('_')[:-1]),
            factorMin=kwargDict[kwargKey][0],
            factorMax=kwargDict[kwargKey][1]) \
         for kwargKey in kwargKeys])
    print("query:",queryStr)
    print("selection shape:",pcaData.query(queryStr).shape)

interactive(children=(FloatRangeSlider(value=(0.0063, 196.48), description='X_bound', max=196.48, min=0.0063),…

In [30]:
@interact_manual
def explore_milestone_bounds( #'D_958', 'D_1178', 'D_1366', 'D_2377', 'D_3796'
    X_bound=widgets.FloatRangeSlider(     min=pcaData.X.min()-.1,max=pcaData.X.max()+.1,
                                   value=(pcaData.X.min()-.1,pcaData.X.max()+.1)),
    
    Y_bound=widgets.FloatRangeSlider(     min=pcaData.Y.min()-.1,max=pcaData.Y.max()+.1,
                                   value=(pcaData.Y.min()-.1,pcaData.Y.max()+.1)),
    
    Z_bound=widgets.FloatRangeSlider(     min=pcaData.Z.min()-.1,max=pcaData.Z.max()+.1,
                                   value=(pcaData.Z.min()-.1,pcaData.Z.max()+.1)),
    
    D_958_bound=widgets.FloatRangeSlider( min=pcaData.D_958.min()-.1,max=pcaData.D_958.max()+.1,
                                   value=(pcaData.D_958.min()-.1,pcaData.D_958.max()+.1)),
    
    D_1178_bound=widgets.FloatRangeSlider(min=pcaData.D_1178.min()-.1,max=pcaData.D_1178.max()+.1,
                                   value=(pcaData.D_1178.min()-.1,pcaData.D_1178.max()+.1)),
    
    D_1366_bound=widgets.FloatRangeSlider(min=pcaData.D_1366.min()-.1,max=pcaData.D_1366.max()+.1,
                                   value=(pcaData.D_1366.min()-.1,pcaData.D_1366.max()+.1)),
    
    D_2377_bound=widgets.FloatRangeSlider(min=pcaData.D_2377.min()-.1,max=pcaData.D_2377.max()+.1,
                                   value=(pcaData.D_2377.min()-.1,pcaData.D_2377.max()+.1)),
    
    D_3796_bound=widgets.FloatRangeSlider(min=pcaData.D_3796.min()-.1,max=pcaData.D_3796.max()+.1,
                                   value=(pcaData.D_3796.min()-.1,pcaData.D_3796.max()+.1)),
    
    PCA_0_bound=widgets.FloatRangeSlider( min=pcaData.PCA_0.min()-.1,max=pcaData.PCA_0.max()+.1,
                                   value=(pcaData.PCA_0.min()-.1,pcaData.PCA_0.max()+.1)),
    
    PCA_1_bound=widgets.FloatRangeSlider( min=pcaData.PCA_1.min()-.1,max=pcaData.PCA_1.max()+.1,
                                   value=(pcaData.PCA_1.min()-.1,pcaData.PCA_1.max()+.1)),
    
    PCA_2_bound=widgets.FloatRangeSlider( min=pcaData.PCA_1.min()-.1,max=pcaData.PCA_1.max()+.1,
                                   value=(pcaData.PCA_1.min()-.1,pcaData.PCA_1.max()+.1)),
    
    PCA_3_bound=widgets.FloatRangeSlider( min=pcaData.PCA_3.min()-.1,max=pcaData.PCA_3.max()+.1,
                                   value=(pcaData.PCA_3.min()-.1,pcaData.PCA_3.max()+.1)),
    
    PCA_4_bound=widgets.FloatRangeSlider( min=pcaData.PCA_4.min(),max=pcaData.PCA_4.max(),
                                   value=(pcaData.PCA_4.min(),pcaData.PCA_4.max())),
    xCol=widgets.Dropdown(options=pcaData.columns[3:],value='X'),
    yCol=widgets.Dropdown(options=pcaData.columns[3:],value='Y'),
    zCol=widgets.Dropdown(options=pcaData.columns[3:],value='Z'),
    verbose=widgets.ToggleButton(value=False)
    ):
    kwargDict=dict(locals())
    if verbose:
        print(kwargDict.keys(),kwargDict.values())
    kwargDict=dict(locals())
    kwargKeys=np.array(list(kwargDict.keys()))[:13]
    if verbose:
        for kwargKey in kwargKeys:
            print(kwargKey,end="")
            print(len(kwargDict[kwargKey]),kwargDict[kwargKey][0],kwargDict[kwargKey][1])
    queryStr=' and '.join(
        ['({factorKey:s} >= {factorMin:f}) and ({factorKey:s} <= {factorMax:f})'.format(
            factorKey='_'.join(kwargKey.split('_')[:-1]),
            factorMin=kwargDict[kwargKey][0],
            factorMax=kwargDict[kwargKey][1]) \
         for kwargKey in kwargKeys])
    if verbose:
        print("query:",queryStr)
        print("selection shape:",pcaData.query(queryStr).shape)
    go=ply.graph_objs
    fig=go.Figure(
        data=[
                go.Scatter3d(x=pcaData.query('AtomType == "POT"')[xCol],
                             y=pcaData.query('AtomType == "POT"')[yCol],
                             z=pcaData.query('AtomType == "POT"')[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color='grey',
                                         opacity=.0625)),
                go.Scatter3d(x=pcaData.query(queryStr)[xCol],
                             y=pcaData.query(queryStr)[yCol],
                             z=pcaData.query(queryStr)[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color='blue',
                                         opacity=.25)),
                go.Scatter3d(
                    x=pcaData.query(
                            '(AtomType == "CA")'
                        )[xCol],
                    y=pcaData.query(
                            '(AtomType == "CA")'
                        )[yCol],
                    z=pcaData.query(
                            '(AtomType == "CA")'
                        )[zCol],
                    mode='markers',
                    marker=dict(size=12,
                                color='black',
                                opacity=.25))
             ],
        layout=dict(
            width=800,height=600)
    )
    fig.show()

interactive(children=(FloatRangeSlider(value=(-0.0937, 196.57999999999998), description='X_bound', max=196.579…

# Compute Cylindrical Coordinates

In [31]:
import math
tqdm.tqdm.pandas(tqdm.tqdm_notebook)

In [32]:
diffCoords.query('AtomType=="CA"').head()

Frame  AtomID AtomType         X         Y         Z      D_958     D_1178  \
0      1     958       CA  123.2928  110.9940   58.3107   0.000000  92.177611   
1      1    1178       CA   76.6708  159.4728  121.3417  92.177611   0.000000   
2      1    1366       CA   95.1964  126.0866   32.3294  41.136629  96.855696   
3      1    2377       CA   53.3092  115.8309   59.7553  70.165424  79.014331   
4      1    3796       CA  103.7853  171.4280   55.4642  63.568180  72.235503   

      D_1366     D_2377     D_3796  
0  41.136629  70.165424  63.568180  
1  96.855696  79.014331  72.235503  
2   0.000000  51.106721  51.621998  
3  51.106721   0.000000  75.214944  
4  51.621998  75.214944   0.000000

In [153]:
tqdm.tqdm.pandas(tqdm.tqdm_notebook)
cylCenters=diffCoords.query('AtomType=="CA"')[['Frame','X','Y','Z']].groupby(
    ['Frame']).progress_aggregate(np.mean)
diffCyl=diffCoords.set_index(['Frame']).join(
    cylCenters,rsuffix='_Center',how='outer')
diffCyl=diffCyl.reset_index()
diffCyl['R']=np.sqrt(
        (diffCyl['X']-diffCyl['X_Center'])**2 + \
        (diffCyl['Y']-diffCyl['Y_Center'])**2)
diffCyl['Theta']=np.arctan2(diffCyl['Y']-diffCyl['Y_Center'],diffCyl['X']-diffCyl['X_Center'])
diffCyl=diffCyl[np.concatenate([
    diffCyl.columns[:6],
    [colName for colName in diffCyl.columns if '_Center' in colName],
    ['R','Theta'],
    [colName for colName in diffCyl.columns if 'D_' in colName],
])]
print(diffCyl.shape)
diffCyl.head()

C:\ProgramData\Anaconda3\lib\site-packages\tqdm\std.py:658: FutureWarning:

The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version

100%|██████████| 2081/2081 [00:00<00:00, 8025.22it/s] 


(43701, 16)


Frame  AtomID AtomType         X         Y         Z  X_Center   Y_Center  \
0      1     958       CA  123.2928  110.9940   58.3107   90.4509  136.76246   
1      1    1178       CA   76.6708  159.4728  121.3417   90.4509  136.76246   
2      1    1366       CA   95.1964  126.0866   32.3294   90.4509  136.76246   
3      1    2377       CA   53.3092  115.8309   59.7553   90.4509  136.76246   
4      1    3796       CA  103.7853  171.4280   55.4642   90.4509  136.76246   

   Z_Center          R     Theta      D_958     D_1178     D_1366     D_2377  \
0  65.44026  41.744508 -0.665293   0.000000  92.177611  41.136629  70.165424   
1  65.44026  26.564087  2.116184  92.177611   0.000000  96.855696  79.014331   
2  65.44026  11.683054 -1.152519  41.136629  96.855696   0.000000  51.106721   
3  65.44026  42.633743 -2.628399  70.165424  79.014331  51.106721   0.000000   
4  65.44026  37.141700  1.203585  63.568180  72.235503  51.621998  75.214944   

      D_3796  
0  63.568180  
1  72.235503  
2  51.621998  
3  75.214944  
4   0.000000

## Explore radial cutoff

In [34]:
@interact_manual
def explore_milestone_bounds( #'D_958', 'D_1178', 'D_1366', 'D_2377', 'D_3796'
    R_bound=widgets.FloatRangeSlider(     min=0,max=diffCyl.R.max()+.1,
                                   value=(0,diffCyl.R.max()+.1)),
    
    Theta_bound=widgets.FloatRangeSlider(     min=-np.pi,max=np.pi,
                                   value=(-np.pi,np.pi)),
    
    Z_bound=widgets.FloatRangeSlider(     min=diffCyl.Z.min()-.1,max=diffCyl.Z.max()+.1,
                                   value=(diffCyl.Z.min()-.1,diffCyl.Z.max()+.1)),
    xCol=widgets.Dropdown(options=diffCyl.columns[3:],value='X'),
    yCol=widgets.Dropdown(options=diffCyl.columns[3:],value='Y'),
    zCol=widgets.Dropdown(options=diffCyl.columns[3:],value='Z'),
    showCenter=widgets.ToggleButton(value=True),
    verbose=widgets.ToggleButton(value=False)
    ):
    kwargDict=dict(locals())
    if verbose:
        print(kwargDict.keys(),kwargDict.values())
    kwargDict=dict(locals())
    kwargKeys=np.array(list(kwargDict.keys()))[:3]
    if verbose:
        for kwargKey in kwargKeys:
            print(kwargKey,end="")
            print(len(kwargDict[kwargKey]),kwargDict[kwargKey][0],kwargDict[kwargKey][1])
    queryStr=' and '.join(
        ['({factorKey:s} >= {factorMin:f}) and ({factorKey:s} <= {factorMax:f})'.format(
            factorKey='_'.join(kwargKey.split('_')[:-1]),
            factorMin=kwargDict[kwargKey][0],
            factorMax=kwargDict[kwargKey][1]) \
         for kwargKey in kwargKeys])
    if verbose:
        print("query:",queryStr)
        print("selection shape:",diffCyl.query(queryStr).shape)
        print(diffCyl.query(queryStr).head())
    go=ply.graph_objs
    plotData=[
                go.Scatter3d(x=diffCyl.query(
                                    'AtomType == "POT"'
                                 ).query("not ("+queryStr+")")[xCol],
                             y=diffCyl.query(
                                     'AtomType == "POT"'
                                 ).query("not ("+queryStr+")")[yCol],
                             z=diffCyl.query(
                                     'AtomType == "POT"'
                                 ).query("not ("+queryStr+")")[zCol],
                             mode='markers',
                             marker=dict(size=24,
                                         color='grey',
                                         opacity=.0625)),
                go.Scatter3d(x=diffCyl.query(queryStr)[xCol],
                             y=diffCyl.query(queryStr)[yCol],
                             z=diffCyl.query(queryStr)[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color='blue',
                                         opacity=.25)),
                go.Scatter3d(
                    x=diffCyl.query(
                            '(AtomType == "CA")'
                        )[xCol],
                    y=diffCyl.query(
                            '(AtomType == "CA")'
                        )[yCol],
                    z=diffCyl.query(
                            '(AtomType == "CA")'
                        )[zCol],
                    mode='markers',
                    marker=dict(size=12,
                                color='black',
                                opacity=.25))
             ]
    if showCenter:
        plotData.append(
                go.Scatter3d(x=diffCyl.query('AtomType == "CA"')['X_Center'],
                             y=diffCyl.query('AtomType == "CA"')['Y_Center'],
                             z=diffCyl.query('AtomType == "CA"')['Z_Center'],
                             mode='markers',
                             marker=dict(size=12,
                                         color='red',
                                         opacity=.5)))
    fig=go.Figure(
        data=plotData,
        layout=dict(
            width=800,height=600)
    )
    fig.show()

interactive(children=(FloatRangeSlider(value=(0.0, 171.15737440875327), description='R_bound', max=171.1573744…

## Apply Cylindrical Filter

In [154]:
queryEntry="(R >= 0.000000) and (R <= 171.000000) and (Theta >= -3.141593) and (Theta <= 3.141593) and (Z >= 0.000000) and (Z <= 145)"
cylData=diffCyl.query(queryEntry)
print(cylData.shape,diffCoords.shape)
display(diffCyl.query("not ("+queryEntry+")"))
cylData.head()

(43700, 16) (43701, 11)


Frame  AtomID AtomType         X       Y        Z  X_Center  Y_Center  \
509     25  165530      POT  194.4881  1.2067  12.1098  92.17352  138.2919   

     Z_Center           R    Theta       D_958      D_1178      D_1366  \
509  64.04378  171.057374 -0.92963  136.709467  226.560729  159.858488   

         D_2377      D_3796  
509  187.306998  198.938532

Frame  AtomID AtomType         X         Y         Z  X_Center   Y_Center  \
0      1     958       CA  123.2928  110.9940   58.3107   90.4509  136.76246   
1      1    1178       CA   76.6708  159.4728  121.3417   90.4509  136.76246   
2      1    1366       CA   95.1964  126.0866   32.3294   90.4509  136.76246   
3      1    2377       CA   53.3092  115.8309   59.7553   90.4509  136.76246   
4      1    3796       CA  103.7853  171.4280   55.4642   90.4509  136.76246   

   Z_Center          R     Theta      D_958     D_1178     D_1366     D_2377  \
0  65.44026  41.744508 -0.665293   0.000000  92.177611  41.136629  70.165424   
1  65.44026  26.564087  2.116184  92.177611   0.000000  96.855696  79.014331   
2  65.44026  11.683054 -1.152519  41.136629  96.855696   0.000000  51.106721   
3  65.44026  42.633743 -2.628399  70.165424  79.014331  51.106721   0.000000   
4  65.44026  37.141700  1.203585  63.568180  72.235503  51.621998  75.214944   

      D_3796  
0  63.568180  
1  72.235503  
2  51.621998  
3  75.214944  
4   0.000000

## Compute Filtered PCA projection

In [147]:
import sklearn as skl
from sklearn.decomposition import PCA

In [155]:
queryEntry="(R >= 0.000000) and (R <= 80.000000) and (Theta >= -3.141593) and (Theta <= 3.141593) and (Z >= 0.000000) and (Z <= 140)"
cylData=diffCyl.query(queryEntry)

XCylData=cylData.query('AtomType == "POT"')[cylData.columns[-5:]]

pcaCyl=PCA()
pcaCyl.fit(XCylData)
pcaCyl_coords=pcaCyl.transform(cylData[cylData.columns[-5:]])

pcaCylData=cylData.copy()
for ii in np.arange(pcaCyl_coords.shape[1]):
    pcaCylData['PCAcyl_%g'%ii]=pcaCyl_coords[:,ii]
    
pcaCylData.head()

Frame  AtomID AtomType         X         Y         Z  X_Center   Y_Center  \
0      1     958       CA  123.2928  110.9940   58.3107   90.4509  136.76246   
1      1    1178       CA   76.6708  159.4728  121.3417   90.4509  136.76246   
2      1    1366       CA   95.1964  126.0866   32.3294   90.4509  136.76246   
3      1    2377       CA   53.3092  115.8309   59.7553   90.4509  136.76246   
4      1    3796       CA  103.7853  171.4280   55.4642   90.4509  136.76246   

   Z_Center          R  ...      D_958     D_1178     D_1366     D_2377  \
0  65.44026  41.744508  ...   0.000000  92.177611  41.136629  70.165424   
1  65.44026  26.564087  ...  92.177611   0.000000  96.855696  79.014331   
2  65.44026  11.683054  ...  41.136629  96.855696   0.000000  51.106721   
3  65.44026  42.633743  ...  70.165424  79.014331  51.106721   0.000000   
4  65.44026  37.141700  ...  63.568180  72.235503  51.621998  75.214944   

      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2   PCAcyl_3   PCAcyl_4  
0  63.568180 -37.793808  27.388747 -19.905732 -45.029068  -8.578721  
1  72.235503  35.590037 -82.218968  -5.244114  -0.797064  17.517078  
2  51.621998 -61.828181  31.874860   0.939633   3.330112  14.688390  
3  75.214944 -31.627981  -9.635206  58.098393   6.779326 -17.362311  
4   0.000000 -32.761493 -14.019092 -45.214532  33.429760 -17.449956  

[5 rows x 21 columns]

In [158]:
?np.savetxt

In [159]:
np.savetxt(fname='/'.join([dataDir,'pca_components.cylindricalFilter.txt']),X=pcaCyl.components_)
pcaCylData.to_csv('/'.join([dataDir,'pca_projection_data.cylindricalFilter.csv']),
                  index=False)

# Visualize Cylindrical Filtered PCA projection

In [161]:
dataDir='simulationData'
pcaCylData=pd.read_csv('/'.join([dataDir,'pca_projection_data.cylindricalFilter.csv']))
pcaComponents=np.loadtxt('/'.join([dataDir,'pca_components.cylindricalFilter.txt']))
display(pcaCylData.head())
display(pcaCylData[pcaCylData.columns[3:]].agg(['min','mean','max','std']).T)
display(pcaComponents)

Frame  AtomID AtomType         X         Y         Z  X_Center   Y_Center  \
0      1     958       CA  123.2928  110.9940   58.3107   90.4509  136.76246   
1      1    1178       CA   76.6708  159.4728  121.3417   90.4509  136.76246   
2      1    1366       CA   95.1964  126.0866   32.3294   90.4509  136.76246   
3      1    2377       CA   53.3092  115.8309   59.7553   90.4509  136.76246   
4      1    3796       CA  103.7853  171.4280   55.4642   90.4509  136.76246   

   Z_Center          R  ...      D_958     D_1178     D_1366     D_2377  \
0  65.44026  41.744508  ...   0.000000  92.177611  41.136629  70.165424   
1  65.44026  26.564087  ...  92.177611   0.000000  96.855696  79.014331   
2  65.44026  11.683054  ...  41.136629  96.855696   0.000000  51.106721   
3  65.44026  42.633743  ...  70.165424  79.014331  51.106721   0.000000   
4  65.44026  37.141700  ...  63.568180  72.235503  51.621998  75.214944   

      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2   PCAcyl_3   PCAcyl_4  
0  63.568180 -37.793808  27.388747 -19.905732 -45.029068  -8.578721  
1  72.235503  35.590037 -82.218968  -5.244114  -0.797064  17.517078  
2  51.621998 -61.828181  31.874860   0.939633   3.330112  14.688390  
3  75.214944 -31.627981  -9.635206  58.098393   6.779326 -17.362311  
4   0.000000 -32.761493 -14.019092 -45.214532  33.429760 -17.449956  

[5 rows x 21 columns]

min        mean         max        std
X          12.897700   95.850923  172.923400  28.714918
Y          59.523800  135.896598  219.726600  27.864356
Z           0.001800   65.804663  139.968200  34.760019
X_Center   90.450900   92.723626   93.817320   0.347674
Y_Center  136.762460  139.457834  140.845240   0.508592
Z_Center   61.632960   62.758913   65.440260   0.388478
R           0.084237   34.853375   79.996104  20.166349
Theta      -3.140898   -0.245226    3.141472   1.724236
D_958       0.000000   60.451554  146.410816  27.344729
D_1178      0.000000   74.061380  158.201029  31.873921
D_1366      0.000000   55.870725  142.839902  31.686225
D_2377      0.000000   63.239428  147.475220  28.783890
D_3796      0.000000   62.200603  144.511501  27.316858
PCAcyl_0  -62.930743   -9.303811  127.236062  42.642660
PCAcyl_1  -83.188194   -3.750897   85.143925  35.800885
PCAcyl_2  -47.172715   -0.630560   61.068845  26.746519
PCAcyl_3  -49.206053    0.049699   53.823759  20.691509
PCAcyl_4  -17.955845   -0.545250   18.956200   9.940137

array([[ 0.40045854,  0.08449305,  0.65258185,  0.46235539,  0.43915636],
       [-0.14434161,  0.90046587, -0.30072427,  0.20338675,  0.19111636],
       [ 0.27838328,  0.07815429, -0.03906275, -0.75636341,  0.58547685],
       [ 0.82572275,  0.19911421, -0.15603285, -0.05535959, -0.50112327],
       [ 0.24389168, -0.3691444 , -0.67663114,  0.41195998,  0.42036715]])

In [40]:
@interact_manual
def color_by_distance(colorColumn=widgets.Dropdown(
                          options=[colName for colName in pcaCylData.columns \
                                   if ('PCAcyl_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='PCAcyl_0'),
                      xCol=widgets.Dropdown(
                          options=[colName for colName in pcaCylData.columns \
                                   if ('PCAcyl_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='X'),
                      yCol=widgets.Dropdown(
                          options=[colName for colName in pcaCylData.columns \
                                   if ('PCAcyl_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='Y'),
                      zCol=widgets.Dropdown(
                          options=[colName for colName in pcaCylData.columns \
                                   if ('PCAcyl_' in colName) | ('D_' in colName) | \
                                      (colName=='X') | (colName=='Y') | (colName=='Z')],
                          value='Z'),
                     ):
    go=ply.graph_objs
    fig=go.Figure(
        data=[
                go.Scatter3d(x=pcaCylData.query('AtomType == "POT"')[xCol],
                             y=pcaCylData.query('AtomType == "POT"')[yCol],
                             z=pcaCylData.query('AtomType == "POT"')[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color=pcaCylData.query(
                                                 'AtomType == "POT"'
                                             )[colorColumn],
                                         colorscale='RdBu',
                                         opacity=.125)),
                go.Scatter3d(
                    x=pcaCylData.query(
                            '(AtomType == "CA")'
                        )[xCol],
                    y=pcaCylData.query(
                            '(AtomType == "CA")'
                        )[yCol],
                    z=pcaCylData.query(
                            '(AtomType == "CA")'
                        )[zCol],
                    mode='markers',
                    marker=dict(size=12,
                                color='black',
                                opacity=.25))
             ],
        layout=dict(
            width=800,height=600)
    )
    fig.show()

interactive(children=(Dropdown(description='colorColumn', index=8, options=('X', 'Y', 'Z', 'D_958', 'D_1178', …

In [60]:
@interact_manual
def explore_milestone_bounds( #'D_958', 'D_1178', 'D_1366', 'D_2377', 'D_3796'
    X_bound=widgets.FloatRangeSlider(     min=pcaCylData.X.min()-1.,max=pcaCylData.X.max()+1.,
                                   value=(pcaCylData.X.min()-1.,pcaCylData.X.max()+1.)),
    
    Y_bound=widgets.FloatRangeSlider(     min=pcaCylData.Y.min()-1.,max=pcaCylData.Y.max()+1.,
                                   value=(pcaCylData.Y.min()-1.,pcaCylData.Y.max()+1.)),
    
    Z_bound=widgets.FloatRangeSlider(     min=pcaCylData.Z.min()-1.,max=pcaCylData.Z.max()+1.,
                                   value=(pcaCylData.Z.min()-1.,pcaCylData.Z.max()+1.)),
    
    R_bound=widgets.FloatRangeSlider(     min=0,max=pcaCylData.R.max()+1.,
                                   value=(0,pcaCylData.R.max()+1.)),
    
    Theta_bound=widgets.FloatRangeSlider(     min=-np.pi,max=np.pi,
                                   value=(-np.pi,np.pi)),
    
    D_958_bound=widgets.FloatRangeSlider( min=pcaCylData.D_958.min()-1.,max=pcaCylData.D_958.max()+1.,
                                   value=(pcaCylData.D_958.min()-1.,pcaCylData.D_958.max()+1.)),
    
    D_1178_bound=widgets.FloatRangeSlider(min=pcaCylData.D_1178.min()-1.,max=pcaCylData.D_1178.max()+1.,
                                   value=(pcaCylData.D_1178.min()-1.,pcaCylData.D_1178.max()+1.)),
    
    D_1366_bound=widgets.FloatRangeSlider(min=pcaCylData.D_1366.min()-1.,max=pcaCylData.D_1366.max()+1.,
                                   value=(pcaCylData.D_1366.min()-1.,pcaCylData.D_1366.max()+1.)),
    
    D_2377_bound=widgets.FloatRangeSlider(min=pcaCylData.D_2377.min()-1.,max=pcaCylData.D_2377.max()+1.,
                                   value=(pcaCylData.D_2377.min()-1.,pcaCylData.D_2377.max()+1.)),
    
    D_3796_bound=widgets.FloatRangeSlider(min=pcaCylData.D_3796.min()-1.,max=pcaCylData.D_3796.max()+1.,
                                   value=(pcaCylData.D_3796.min()-1.,pcaCylData.D_3796.max()+1.)),
    
    PCAcyl_0_bound=widgets.FloatRangeSlider( min=pcaCylData.PCAcyl_0.min()-1.,max=pcaCylData.PCAcyl_0.max()+1.,
                                   value=(pcaCylData.PCAcyl_0.min()-1.,pcaCylData.PCAcyl_0.max()+1.)),
    
    PCAcyl_1_bound=widgets.FloatRangeSlider( min=pcaCylData.PCAcyl_1.min()-1.,max=pcaCylData.PCAcyl_1.max()+1.,
                                   value=(pcaCylData.PCAcyl_1.min()-1.,pcaCylData.PCAcyl_1.max()+1.)),
    
    PCAcyl_2_bound=widgets.FloatRangeSlider( min=pcaCylData.PCAcyl_1.min()-1.,max=pcaCylData.PCAcyl_1.max()+1.,
                                   value=(pcaCylData.PCAcyl_1.min()-1.,pcaCylData.PCAcyl_1.max()+1.)),
    
    PCAcyl_3_bound=widgets.FloatRangeSlider( min=pcaCylData.PCAcyl_3.min()-1.,max=pcaCylData.PCAcyl_3.max()+1.,
                                   value=(pcaCylData.PCAcyl_3.min()-1.,pcaCylData.PCAcyl_3.max()+1.)),
    
    PCAcyl_4_bound=widgets.FloatRangeSlider( min=pcaCylData.PCAcyl_4.min(),max=pcaCylData.PCAcyl_4.max(),
                                   value=(pcaCylData.PCAcyl_4.min(),pcaCylData.PCAcyl_4.max())),
    
    xCol=widgets.Dropdown(options=pcaCylData.columns[3:],value='X'),
    yCol=widgets.Dropdown(options=pcaCylData.columns[3:],value='Y'),
    zCol=widgets.Dropdown(options=pcaCylData.columns[3:],value='Z'),
    verbose=widgets.ToggleButton(value=False),
    showCutRegions=widgets.ToggleButton(value=False),
    ):
    kwargDict=dict(locals())
    if verbose:
        print(kwargDict.keys(),kwargDict.values())
    kwargDict=dict(locals())
    kwargKeys=np.array(list(kwargDict.keys()))[:15]
    if verbose:
        for kwargKey in kwargKeys:
            print(kwargKey,end="")
            print(len(kwargDict[kwargKey]),kwargDict[kwargKey][0],kwargDict[kwargKey][1])
    queryStr=' and '.join(
        ['({factorKey:s} >= {factorMin:f}) and ({factorKey:s} <= {factorMax:f})'.format(
            factorKey='_'.join(kwargKey.split('_')[:-1]),
            factorMin=kwargDict[kwargKey][0],
            factorMax=kwargDict[kwargKey][1]) \
         for kwargKey in kwargKeys])
    if verbose:
        print("query:",queryStr)
        print("selection shape:",pcaCylData.query(queryStr).shape)
    go=ply.graph_objs
    fig=go.Figure(
        data=[
                go.Scatter3d(x=pcaCylData.query('AtomType == "POT"')[xCol],
                             y=pcaCylData.query('AtomType == "POT"')[yCol],
                             z=pcaCylData.query('AtomType == "POT"')[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color='grey',
                                         opacity=.0625)),
                go.Scatter3d(x=pcaCylData.query(queryStr)[xCol],
                             y=pcaCylData.query(queryStr)[yCol],
                             z=pcaCylData.query(queryStr)[zCol],
                             mode='markers',
                             marker=dict(size=2,
                                         color='blue',
                                         opacity=.25)),
                go.Scatter3d(
                    x=pcaCylData.query(
                            '(AtomType == "CA")'
                        )[xCol],
                    y=pcaCylData.query(
                            '(AtomType == "CA")'
                        )[yCol],
                    z=pcaCylData.query(
                            '(AtomType == "CA")'
                        )[zCol],
                    mode='markers',
                    marker=dict(size=12,
                                color='black',
                                opacity=.25))
             ],
        layout=dict(
            width=900,height=675)
    )
    fig.show()
    if showCutRegions:
        aggCols=['_'.join(keyName.split('_')[:-1]) for keyName in kwargKeys]
        summaryData=pcaCylData.query(
                "AtomType == 'POT'"
            ).query(
                queryStr
            )[aggCols].agg(['min','max','mean'])
        summaryData=summaryData.T
        #print(summaryData.columns)
        summaryData['Interval']=summaryData['min'].map(str) + \
            ' - '+summaryData['max'].map(str)
        display(summaryData)

interactive(children=(FloatRangeSlider(value=(11.8977, 173.9234), description='X_bound', max=173.9234, min=11.…

# Explore using clustering to find milestone centers

## Generate clusters using agglomerative clustering

In [14]:
dataDir='simulationData'
pcaCylData=pd.read_csv('/'.join([dataDir,'pca_projection_data.cylindricalFilter.csv']))

In [15]:
clust=skl.cluster.AgglomerativeClustering(n_clusters=256)

clustDat=pcaCylData.query('AtomType == "POT"')

Xvals=clustDat[
    #[colName for colName in pcaCylData if 'PCAcyl' in colName]
        #['PCAcyl_2','PCAcyl_3','PCAcyl_1']
        ['X','Y','Z']
    ]
dataInds=pcaCylData.query('AtomType == "POT"').index

clust.fit(Xvals)

xinds=np.arange(len(Xvals))

#reachability=clust.reachability_[clust.ordering_]
#labels=clust.labels_[clust.ordering_]
labels=clust.labels_
clustDat['Cluster']=labels

labelSeries=clustDat['Cluster']
labelSeries.to_csv('/'.join([dataDir,'Agglomerative_Clustering_Labels']))

/Users/wbotellosmith/anaconda2/envs/py3/lib/python3.7/site-packages/ipykernel_launcher.py:19: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

/Users/wbotellosmith/anaconda2/envs/py3/lib/python3.7/site-packages/ipykernel_launcher.py:22: FutureWarning:

The signature of `Series.to_csv` was aligned to that of `DataFrame.to_csv`, and argument 'header' will change its default value from False to True: please pass an explicit value to suppress this warning.



## Load Agglomerative Clustering Results from Disk

In [16]:
dataDir='simulationData'
pcaCylData=pd.read_csv('/'.join([dataDir,'pca_projection_data.cylindricalFilter.csv']))
#labelSeries=pd.Series.from_csv('/'.join([dataDir,'Agglomerative_Clustering_Labels']))
clustDat=pcaCylData.query('AtomType == "POT"')
clustDat['Cluster']=labelSeries
clustDat.to_csv('/'.join([dataDir,'cluster_data.cylindricalFilter.csv']))
clustDat.head()

/Users/wbotellosmith/anaconda2/envs/py3/lib/python3.7/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



Frame  AtomID AtomType         X         Y         Z  X_Center   Y_Center  \
5      1  165552      POT  109.3891   81.3629   25.0487   90.4509  136.76246   
6      1  165554      POT   42.9653   78.8911   51.0144   90.4509  136.76246   
7      1  165557      POT   59.0333   65.9134   93.0642   90.4509  136.76246   
8      1  165570      POT   74.8840  133.9131   21.6081   90.4509  136.76246   
9      1  165581      POT   57.8748  122.7727  107.9835   90.4509  136.76246   

   Z_Center          R  ...      D_1178     D_1366     D_2377      D_3796  \
5  65.44026  58.547132  ...  128.234104  47.483162  74.414691   95.227241   
6  65.44026  74.859712  ...  112.140092  72.832906  39.343976  110.823964   
7  65.44026  77.502612  ...   99.317973  92.829412  60.282709  120.622686   
8  65.44026  15.825525  ...  102.972238  24.265077  47.409354   58.214160   
9  65.44026  35.453007  ...   43.343148  84.424088  48.938661   85.049333   

    PCAcyl_0   PCAcyl_1   PCAcyl_2   PCAcyl_3  PCAcyl_4  Cluster  
5   3.949924  58.126858  10.976897 -16.407481  0.257267      130  
6  25.844157  26.064522  55.562696   3.708095 -9.054124       27  
7  51.407127  14.776168  43.409862  -8.833230 -5.342075       99  
8 -34.763068  27.159143  13.749322  17.308974  3.062724      245  
9  19.177857 -41.791883  26.318759  -2.578299  0.682071        1  

[5 rows x 22 columns]

## Visualize Clusters

In [51]:
plotData=clustDat
plotData['Cluster']=labels
xCol='X'#'PCAcyl_2'
yCol='Y'#'PCAcyl_3'
zCol='Z'#'PCAcyl_1'
nLabels=len(np.unique(labels))
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    scatterPlots.append(
        go.Scatter3d(
                 x=groupData[xCol],
                 y=groupData[yCol],
                 z=groupData[zCol],
                 mode='markers',
                 marker=dict(size=2,
                             color=colorpalette.as_hex()[iGroup],
                             opacity=.25)))

fig=go.Figure(
        data=scatterPlots,
        layout=dict(
            width=900,height=675))
fig.show()

## Compute Cluster Summary and Perform Tesselation / Triangulation

In [71]:
clusterSummary=plotData.groupby('Cluster').agg('mean')
clusterSummary.head()

Frame         AtomID           X           Y           Z  \
Cluster                                                                   
0        1469.468750  165962.562500   44.682934  166.358437  128.804662   
1         928.492063  165651.460317   55.305103  122.662275  111.099722   
2        1030.756098  165566.560976  108.445688  191.335907  111.924205   
3         883.632653  165721.836735  134.698949  156.352233    8.789557   
4        1375.270270  165993.000000   95.947468   99.063916  117.130900   

          X_Center    Y_Center   Z_Center          R     Theta       D_958  \
Cluster                                                                      
0        92.709069  139.608313  62.607678  55.385660  2.627361  121.608573   
1        92.833789  139.335496  62.610575  41.299602 -2.718718   90.101873   
2        92.953200  140.221891  62.604540  53.584732  1.279749   98.816757   
3        92.758402  139.430772  62.830846  45.561842  0.390536   67.557530   
4        92.740730  139.467588  62.735740  40.748084 -1.496197   67.959330   

             D_1178      D_1366      D_2377      D_3796   PCAcyl_0   PCAcyl_1  \
Cluster                                                                         
0         37.869426  118.323749   88.049435   98.259369  80.191258 -52.011713   
1         49.906499   91.289160   55.021504   93.321235  33.509643 -36.156256   
2         41.556516  103.711981  105.311968   60.844022  53.390477 -44.647408   
3        121.596911   52.830699  100.762198   56.624222  10.474347  45.507644   
4         68.521636   92.023583   75.995928  100.809818  39.680890 -10.721619   

          PCAcyl_2   PCAcyl_3   PCAcyl_4  
Cluster                                   
0        13.472579  14.154026  10.851485  
1        28.788391  -0.943710   1.334275  
2       -26.975911  16.142427   5.201749  
3       -26.464210  16.573817  -1.188909  
4        12.570546 -20.549207   0.353862

In [72]:
clusterSummary.to_csv('/'.join([dataDir,'Agglomerative_clustering_centers.csv']))

In [73]:
clusterSummary=pd.read_csv('/'.join([dataDir,'Agglomerative_clustering_centers.csv']))
clusterSummary.head()

Cluster        Frame         AtomID           X           Y           Z  \
0        0  1469.468750  165962.562500   44.682934  166.358437  128.804662   
1        1   928.492063  165651.460317   55.305103  122.662275  111.099722   
2        2  1030.756098  165566.560976  108.445688  191.335907  111.924205   
3        3   883.632653  165721.836735  134.698949  156.352233    8.789557   
4        4  1375.270270  165993.000000   95.947468   99.063916  117.130900   

    X_Center    Y_Center   Z_Center          R  ...       D_958      D_1178  \
0  92.709069  139.608313  62.607678  55.385660  ...  121.608573   37.869426   
1  92.833789  139.335496  62.610575  41.299602  ...   90.101873   49.906499   
2  92.953200  140.221891  62.604540  53.584732  ...   98.816757   41.556516   
3  92.758402  139.430772  62.830846  45.561842  ...   67.557530  121.596911   
4  92.740730  139.467588  62.735740  40.748084  ...   67.959330   68.521636   

       D_1366      D_2377      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2  \
0  118.323749   88.049435   98.259369  80.191258 -52.011713  13.472579   
1   91.289160   55.021504   93.321235  33.509643 -36.156256  28.788391   
2  103.711981  105.311968   60.844022  53.390477 -44.647408 -26.975911   
3   52.830699  100.762198   56.624222  10.474347  45.507644 -26.464210   
4   92.023583   75.995928  100.809818  39.680890 -10.721619  12.570546   

    PCAcyl_3   PCAcyl_4  
0  14.154026  10.851485  
1  -0.943710   1.334275  
2  16.142427   5.201749  
3  16.573817  -1.188909  
4 -20.549207   0.353862  

[5 rows x 21 columns]

In [91]:
tessellationClusters=clusterSummary.index.to_numpy() #[0,1,2,3,4,8,10] 
centeroidColumns=np.concatenate([
    ['Cluster'],
    clusterSummary.columns[3:6],
    clusterSummary.columns[11:]])
tessellationCoordinateColumns=['PCAcyl_2','PCAcyl_3','PCAcyl_1'] #[colName for colName in clusterCenteroids.columns \
                               #if 'PCAcyl' in colName]


clusterCenteroids=clusterSummary
tessellationData=clusterCenteroids[
        clusterCenteroids['Cluster'].isin(tessellationClusters)
    ][tessellationCoordinateColumns]
clusterVoronoi=sp.spatial.Voronoi(tessellationData)
clusterDelaunay=sp.spatial.Delaunay(tessellationData)
print('cluster centeroids')
display(clusterCenteroids)
print('cluster vertices')
print(clusterDelaunay.vertices)
print()
print("cluster adjacency")
neiList=defaultdict(set)
for p in clusterDelaunay.vertices:
    for i,j in itertools.combinations(p,2):
        neiList[tessellationClusters[i]].add(tessellationClusters[j])
        neiList[tessellationClusters[j]].add(tessellationClusters[i])

for key in sorted(neiList.keys()):
    print("%d:%s" % (key,','.join([str(i) for i in neiList[key]])))

cluster centeroids


Cluster        Frame         AtomID           X           Y           Z  \
0          0  1469.468750  165962.562500   44.682934  166.358437  128.804662   
1          1   928.492063  165651.460317   55.305103  122.662275  111.099722   
2          2  1030.756098  165566.560976  108.445688  191.335907  111.924205   
3          3   883.632653  165721.836735  134.698949  156.352233    8.789557   
4          4  1375.270270  165993.000000   95.947468   99.063916  117.130900   
..       ...          ...            ...         ...         ...         ...   
251      251   706.161290  165756.193548   51.901384  137.112374  106.837881   
252      252   635.434783  165692.608696   19.898983  118.408770   99.818748   
253      253  1792.925926  166071.407407  108.690596  100.968807  115.242111   
254      254  1380.769231  165932.038462   56.438638  126.412912   10.929746   
255      255  1727.666667  165992.518519  116.888822  213.585833   36.811437   

      X_Center    Y_Center   Z_Center          R  ...       D_958      D_1178  \
0    92.709069  139.608313  62.607678  55.385660  ...  121.608573   37.869426   
1    92.833789  139.335496  62.610575  41.299602  ...   90.101873   49.906499   
2    92.953200  140.221891  62.604540  53.584732  ...   98.816757   41.556516   
3    92.758402  139.430772  62.830846  45.561842  ...   67.557530  121.596911   
4    92.740730  139.467588  62.735740  40.748084  ...   67.959330   68.521636   
..         ...         ...        ...        ...  ...         ...         ...   
251  92.456301  138.832946  63.324074  40.753408  ...   92.815784   40.099890   
252  92.737587  139.159924  62.809383  75.796665  ...  115.024905   77.713459   
253  92.791507  139.777509  62.660913  42.020837  ...   60.883845   70.709397   
254  92.561277  139.216290  62.823223  38.758145  ...   85.149711  115.214266   
255  92.588433  139.407601  62.737716  78.129681  ...  105.634922  100.368304   

         D_1366      D_2377      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2  \
0    118.323749   88.049435   98.259369  80.191258 -52.011713  13.472579   
1     91.289160   55.021504   93.321235  33.509643 -36.156256  28.788391   
2    103.711981  105.311968   60.844022  53.390477 -44.647408 -26.975911   
3     52.830699  100.762198   56.624222  10.474347  45.507644 -26.464210   
4     92.023583   75.995928  100.809818  39.680890 -10.721619  12.570546   
..          ...         ...         ...        ...        ...        ...   
251   88.902974   53.744565   84.494619  27.744016 -46.607542  24.668731   
252  104.289743   56.176908  112.430294  63.249795 -14.737012  47.705947   
253   90.193080   81.170257   97.813726  36.914376  -6.700063   5.175521   
254   45.384938   46.942317   80.858865  -2.120087  33.145514  33.121392   
255   87.797644  114.851953   43.497343  47.497608  10.737356 -37.231572   

      PCAcyl_3   PCAcyl_4  
0    14.154026  10.851485  
1    -0.943710   1.334275  
2    16.142427   5.201749  
3    16.573817  -1.188909  
4   -20.549207   0.353862  
..         ...        ...  
251   4.210829   2.994330  
252  13.504091  -3.139788  
253 -24.455400  -0.068655  
254  21.825892  -1.488360  
255  44.130458  -7.439146  

[256 rows x 21 columns]

cluster vertices
[[  5 173 138  89]
 [228   5 173 138]
 [162 252 147 113]
 ...
 [230  22  54 144]
 [230 177   6 151]
 [230 177 144 151]]

cluster adjacency
0:32,96,34,167,199,43,237,110,239,121,61,62,127
1:33,69,7,72,233,235,115,85,247,185,251,93,31
2:224,167,40,9,11,109,60,239,92,142,148,188
3:164,136,234,45,46,78,17,23,125,95
4:67,135,202,14,47,16,240,81,83,180,182,186,28,253,191
5:228,138,204,173,17,23,216,89,30,255
6:230,7,231,199,137,235,236,109,237,47,177,114,213,151,59,190
7:1,6,137,151,31,32,34,185,59,61,197,199,233,235,110,247,121,251,127
8:97,162,66,196,198,38,241,50,119,254
9:224,2,165,197,40,137,236,60,142,207,51,155,92,190,127
10:99,100,227,70,105,170,28,240,241,16,83,19,181,249,220,254
11:96,2,40,73,239,92,210,148,188,62,255
12:64,134,231,106,108,140,143,207,179,117,214,215,25,155,189
13:37,166,135,76,204,206,111,176,81,212,55,87,63,126,159
14:67,4,101,154,104,235,47,16,83,180,150,182,151,186,28
15:193,100,70,141,240,145,244,245,217,220,63,126,223
16:194,227,100,101,4,135

## Visualize triangulation of cluster centers

xCol='X'
yCol='Y'
zCol='Z'

plotData=clusterCenteroids
nLabels=np.max(labels)+2
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    scatterPlots.append(
        go.Scatter3d(
                 x=groupData[xCol],
                 y=groupData[yCol],
                 z=groupData[zCol],
                 name='Center_%g'%kClass,
                 mode='markers',
                 marker=dict(size=8,
                             symbol='circle-open',
                             color=colorpalette.as_hex()[kClass],
                             opacity=.75)))
    
    neighborPoints=neiList[kClass]
    for nbPoint in neighborPoints:
        neighborCenters=plotData[plotData['Cluster'].isin([kClass,nbPoint])]
        scatterPlots.append(
            go.Scatter3d(
                x=neighborCenters[xCol],
                y=neighborCenters[yCol],
                z=neighborCenters[zCol],
                name='%g - %g'%(kClass,nbPoint),
                mode='lines',
                line=dict(color='black')
            )
        )

plotData=clustDat
#plotData['Cluster']=labels
nLabels=np.max(labels)+2
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
#scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    scatterPlots.append(
        go.Scatter3d(
                 x=groupData[xCol],
                 y=groupData[yCol],
                 z=groupData[zCol],
                 mode='markers',
                 name='Cluster_%g'%kClass,
                 marker=dict(size=4,
                             color=colorpalette.as_hex()[kClass],
                             opacity=.125)))

fig=go.Figure(
        data=scatterPlots,
        layout=dict(
            width=900,height=675,
            scene = dict(
                    xaxis_title=xCol,
                    yaxis_title=yCol,
                    zaxis_title=zCol)))

fig.show()

## Cell Boundary / Occupancy derivation

The boundary equations / restraints for each cell can be modeled based upon the triangulation. 
Specifically, for each pair of connected cells, we can construct an inclusion test by taking the midpoint
of the two cell centers then computing the normal vector, n, directed from the midpoint, m, between the two cell centers c1 and c2 to a given cell center (either c1 or c2) i.e. n1 = c1-m, n2 = c2-m. Then any point in space, r, we say that r is on the same side of the dividing plane as cell 1 if dot( (r-m), n1 )>0 or r is in on the same side of the dividing plane as cell 2 if dot( (r-m), n2 ) >0.

From here we can then compute cell occupancy conditions for each cell as the union over all the half plane inclusion conditions for that cell center to each connected cell.

So for an N dimensional triangulation, each half plane inclusion condition is defined by a set of 2N numbers, the first N define the coordinates of the centeroid, m, and the second N define the normal vector n pointing from m to the cell being considered.

So for a given central cell, i, and test cell, j, we can compute whether coordinate r is cloer to i than to j:
<font size=4> 
$$
    \delta_{ij} = [(r-c_{ij}) \cdot (R_i-c_{ij})>0] \tag{1}
$$
</font>
where $\delta_{ij}$ is equal to 1 if $r$ is closer to $i$ than to $j$ and 0 if not, $c_{ij}$ is the position vector of the midpoint between cell i and cell j, and $R_i$ is the position vector of cell i

Using this we can then test each point ion coordinate from our data set to determine which cells it belongs to (i.e. for which cells does it pass all half plane inclusion tests).
Importantly, this will allow us to make sure that no ion coordinates belong to more than one cell.

Then, we can plot our cell occupancy as above and color any ion coordinates that occupy multiply cells in red.

As an important note, the inclusion equation above can be expressed as a linear combination of triangulation space coordinates (Distance PCA modes) plus / minus a constant. And since the triangulation space coordinates, being distance PCA modes, are themselves linear combinations of our distances, the inclusion equations can be recast as intervals over LCOD restraints using our defined distances!

To begin, we first note that we will need to recast our above expression in terms of an inequality over some linear combination of distance coordinates, while at present we have an inequality involving the dotproduct of vectors in PCA space, the bases of which are linear combinations of the distance coordinates.

To accomplish this derivation, we first convert from vector dot product notation into an explicit summation over PCA modes, then recast into LCOD notation recasting each PCA mode as a sum over distance coordinates.

To get $\delta_{ij}$ as an explicit sum over every PCA mode, $k$, we write:

<font size=4>
$$
\begin{align}
\delta_{ij} & = [((r-c_{ij}) \cdot (R_i-c_{ij})) & > 0] \nonumber \\
& = [(\sum\limits_{k \in PCAmodes}{r_k R_{ik}-r_k c_{ijk}-c_{ijk} p_{ik}+c_{ijk}^2 }) & > 0] \nonumber \\
& = [(\sum\limits_{k \in PCAmodes}{ r_k (R_{ik} - c_{ijk}) - c_{ijk} R_{ijk} + c_{ijk}^2 }) & > 0] \tag{2}  
\end{align} 
$$
</font>

We now need to convert $r_k$ from the PCA space coordinates into its equivalent under our distance based coordinates, $r_D$, which is what will be used for our restraints. To do this, we use the fact that each principal component mode $k$ is itself a linear combination (i.e. weighted sum) over all distance coordinates $D$. I.e.:

<font size=4> 
$$
    r_k = \sum\limits_{D \in Distances}{\alpha_{kD} (r_D - \hat{\lambda_D})} \tag{3}
$$
</font>
where $\alpha_{kD}$ is the component (coefficient) for distance $D$ under PCA mode $k$, $r_D$ is the position measured in terms of our defined distance measurements as discussed above, and $\hat{\lambda_D}$ is the mean of the measured distance coordinate from PCA.
We now replace $r_k$ in equation <b>(2)</b> with the above expression:

<font size=2>
$$
\begin{align}
\delta_{ij} & = [(\sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances}{ \alpha_{kD}(r_{D} - \hat{\lambda_D}))(R_{ik} - c_{ijk}) - c_{ijk} R_{ijk} + c_{ijk}^2 }})) & > 0] \nonumber \\
& = [({\sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances} \alpha_{kD}(R_{ik} - c_{ijk})(r_{D}-\hat{\lambda_D}))} - \sum\limits_{k \in PCAmodes}{c_{ijk} R_{ijk} + c_{ijk}^2 }})) & > 0] \nonumber \\
& = [({\sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances} \alpha_{kD}(R_{ik} - c_{ijk})r_{D}-\alpha_{kD}(R_{ik} - c_{ijk})\hat{\lambda_D})} - \sum\limits_{k \in PCAmodes}{c_{ijk} R_{ijk} + c_{ijk}^2 }})) & > 0] \nonumber \\
& = [({\sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances}{\alpha_{kD}(R_{ik} - c_{ijk})r_{D})}}) - (\sum\limits_{k \in PCAmodes}{c_{ijk} R_{ijk} + c_{ijk}^2 + (\sum\limits_{D \in Distances}{ \alpha_{kD}(R_{ik} - c_{ijk})\hat{\lambda_D}}}}))) & > 0] \nonumber \\
& = [({\sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances}{\alpha_{kD}(R_{ik} - c_{ijk})r_{D})}}) - (\sum\limits_{k \in PCAmodes}{(c_{ijk} R_{ijk} + c_{ijk}^2 + (R_{ik} - c_{ijk})(\sum\limits_{D \in Distances}{ \alpha_{kD}\hat{\lambda_D}}})}))) & > 0] \tag{4} 
\end{align} 
$$
</font>

Where $\alpha_{kD}$ is the coefficient for the $D$'th distance in the $k$'th principal component mode.

Notice that the last equation <b>(4)</b> was deliberately rearranged on the second line to emphasize that the summation only affects the $r_D$ term and the coefficient of that term is now clearly recognizable as $\alpha_{kD}(R_{ik} - c_{ijk})$.

We can now derive our LCOD restraint by decomposing the right hand side expression of equation <B>(4)</B> into a LCOD coefficient term and an interval bound term. Lets rearrange this a bit to make our interval condition more clear. We will rearrange our inequality so that the term containing D is isolated on the left hand side.

<font size=3>
$$
\delta_{ij} = [(\sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances} \alpha_{kD}(R_{ik} - c_{ijk})r_{D}) } ) >  \sum\limits_{k \in PCAmodes}{(c_{ijk} R_{ijk} + c_{ijk}^2 + (R_{ik} - c_{ijk})(\sum\limits_{D \in Distances}{ \alpha_{kD}\hat{\lambda_D}}))} ] \tag{5} 
$$
</font>

We now have our LCOD collective variable and its corresponding interval limit clearly isolated. The expression we will use to derive our LCOD collective variable is on the left hand side of the inequality, while the expression that will be used to derive the interval over this collective variable is on the right hand side of the inequality.

Next we need to derive the individual LCOD coefficients, $\kappa_{ijD}$ for distance D so that we may clearly define our LCOD restraint which will be used to restrain our ion to be closer to cell $i$ than cell $j$. We do so by recognize that our LCOD restraint collective variable should take the form:
<font size=4>
$$
\begin{align}
    LCOD_{ij} & = \sum\limits_{k \in PCAmodes}{(\sum\limits_{D \in Distances} \alpha_{kD}(R_{ik} - c_{ijk})r_{D}) } \nonumber \\
    LCOD_{ij} & = \sum\limits_{D \in Distances}{(\sum\limits_{k \in PCAmodes} \alpha_{kD}(R_{ik} - c_{ijk})r_{D}) } \tag{6}
\end{align}
$$
</font>

Our $\kappa_{ijd}$ coefficients are then readily visibile as the terms being summed by the left hand side of the inequallity shown in the last line of equation <b>(4)</b> after swapping the positions of the PCA and distance coordinate summations:

<font size=4>
$$
\begin{align}
    LCOD_{ij} & = \sum\limits_{D \in Distances}{(\sum\limits_{k \in PCAmodes} \alpha_{kD}(R_{ik} - c_{ijk})r_{D}) } \nonumber \\
    & = \sum\limits_{D \in Distances}{\kappa_{ijd}r_D};  \nonumber \\
    where & : \kappa_{ijD} = \sum\limits_{k \in PCAmodes}{\alpha_{kD} (R_{ik} - c_{ijk})} \tag{7}
\end{align}
$$
</font>

and the flat bottom region interval for this LCOD restraint, $LCOD_{ij}$ used to restrain our ion to be closer to cell $i$ than cell $j$ is given as:

<font size=4>
\begin{align}
    LCOD_{ij} > \sum\limits_{k \in PCAmodes}{(c_{ijk} R_{iK} - c_{ijk}^2 + (R_{ik} - c_{ijk})(\sum\limits_{D \in Distances}{ \alpha_{kD}\hat{\lambda_D}}) )} \tag{8} \\
\end{align}
</font>

In [57]:
cTest=[15, 22, 30, 31, 54, 59, 63, 82, 100, 124, 135, 137, 141, 144,
       145, 146, 177, 186, 194, 202, 207, 211, 214, 215, 220, 223, 230]
plotClusters=cTest
xCol='PCAcyl_2' #'X' #
yCol='PCAcyl_3' #'Y' #
zCol='PCAcyl_1' #'Z' #

plotData=clusterCenteroids
nLabels=np.max(labels)+2
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    if kClass in plotClusters:
        scatterPlots.append(
            go.Scatter3d(
                     x=groupData[xCol],
                     y=groupData[yCol],
                     z=groupData[zCol],
                     name='Center_%g'%kClass,
                     mode='markers',
                     marker=dict(size=12,
                                 symbol='circle-open',
                                 color=colorpalette.as_hex()[kClass],
                                 opacity=.75)))

        neighborPoints=neiList[kClass]
        for nbPoint in neighborPoints:
            if nbPoint in plotClusters:
                neighborCenters=plotData[plotData['Cluster'].isin([kClass,nbPoint])]
                scatterPlots.append(
                    go.Scatter3d(
                        x=neighborCenters[xCol],
                        y=neighborCenters[yCol],
                        z=neighborCenters[zCol],
                        name='%g - %g'%(kClass,nbPoint),
                        mode='lines',
                        line=dict(color='black')
                    )
                )

plotData=clustDat
#plotData['Cluster']=labels
nLabels=np.max(labels)+2
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
#scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    if kClass in plotClusters:
        scatterPlots.append(
            go.Scatter3d(
                     x=groupData[xCol],
                     y=groupData[yCol],
                     z=groupData[zCol],
                     mode='markers',
                     name='Cluster_%g'%kClass,
                     marker=dict(size=6,
                                 color=colorpalette.as_hex()[kClass],
                                 opacity=.25)))
    else:
        kClass,groupData=plotGroup
        scatterPlots.append(
            go.Scatter3d(
                     x=groupData[xCol],
                     y=groupData[yCol],
                     z=groupData[zCol],
                     mode='markers',
                     name='Cluster_%g'%kClass,
                     marker=dict(size=2,
                                 color='black',
                                 opacity=.0625)))

fig=go.Figure(
        data=scatterPlots,
        layout=dict(
            width=900,height=675,
            scene = dict(
                    xaxis_title=xCol,
                    yaxis_title=
           yCol,         zaxis_title=zCol)))

fig.show()

In [58]:
cTest=[202,135,211,186,63]

plotClusters=cTest
xCol='PCAcyl_2' #'X' #
yCol='PCAcyl_3' #'Y' #
zCol='PCAcyl_1' #'Z' #

plotData=clusterCenteroids
nLabels=np.max(labels)+2
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    if kClass in plotClusters:
        scatterPlots.append(
            go.Scatter3d(
                     x=groupData[xCol],
                     y=groupData[yCol],
                     z=groupData[zCol],
                     name='Center_%g'%kClass,
                     mode='markers',
                     marker=dict(size=12,
                                 symbol='circle-open',
                                 color=colorpalette.as_hex()[kClass],
                                 opacity=.75)))

        

        neighborPoints=neiList[kClass]
        for nbPoint in neighborPoints:
            if nbPoint in plotClusters:
                neighborCenters=plotData[plotData['Cluster'].isin([kClass,nbPoint])]
                scatterPlots.append(
                    go.Scatter3d(
                        x=neighborCenters[xCol],
                        y=neighborCenters[yCol],
                        z=neighborCenters[zCol],
                        name='%g - %g'%(kClass,nbPoint),
                        mode='lines',
                        line=dict(color='black')
                    )
                )

plotData=clustDat
#plotData['Cluster']=labels
nLabels=np.max(labels)+2
colorpalette=sns.palettes.color_palette('colorblind',nLabels)
go=ply.graph_objs
#scatterPlots=[]
for iGroup,plotGroup in enumerate(plotData.groupby('Cluster')):
    kClass,groupData=plotGroup
    if kClass in plotClusters:
        scatterPlots.append(
            go.Scatter3d(
                     x=groupData[xCol],
                     y=groupData[yCol],
                     z=groupData[zCol],
                     mode='markers',
                     name='Cluster_%g'%kClass,
                     marker=dict(size=6,
                                 color=colorpalette.as_hex()[kClass],
                                 opacity=.25)))
    else:
        kClass,groupData=plotGroup
        scatterPlots.append(
            go.Scatter3d(
                     x=groupData[xCol],
                     y=groupData[yCol],
                     z=groupData[zCol],
                     mode='markers',
                     name='Cluster_%g'%kClass,
                     marker=dict(size=2,
                                 color='black',
                                 opacity=.0625)))

fig=go.Figure(
        data=scatterPlots,
        layout=dict(
            width=900,height=675,
            scene = dict(
                    xaxis_title=xCol,
                    yaxis_title=
           yCol,         zaxis_title=zCol)))

fig.show()

## Define restraint LCOD coefficients and restraint interval boundaries

Each cell will need to have a set of restraints defined that will restrict the motion of our ion to within that cell. These will be defined by constructing linear combinations of our distance vectors which will be restrained to be within some given interval via a flat bottom harmonic well. Such restraints effectively define the half plane restraints we require.

To employ these restraints to a give cell, $i$, we need to calculate a half plane restraint for each connected cell $j$.

Each half plane is defined by a vector, containing the $\kappa_{ijD}$ entries and a scalar describing the upper limit of the half plane along the LCOD vector described by $\vec{\kappa_{ij}}$

Therefore, the set of all needed restraints for cell $i$ can be described by an nRestraints by nDistances matrix / array, $K_i$, describing the LCOD coefficients of each halfplane, and an nRestraints length vector describing the corresponding upper limits of each LCOD variable.

Using this above description, we can then iterate over all of our defined clusters to ensure that our setup assigns each point from our ion coordinate set to the appropriate cluster. This is an important validation because we originally constructed our clusters based on XYZ coordinates, but we seek to restrict them based on linear combinations of distances measured from our 5 control points. Those corresponding LCOD vectors will not describe our 3D space in the same way as our cartesian coordinates, so we need to be careful to ensure that our cell descriptions under the LCOD basis describe the same set of points as the clusters they are seeking to emulate. In fact, they are expected to be imperfect due to the non-linear nature of distance based restraints, what is important, then, is that they are sufficiently similar that we can use them to describe our milestoning simulation properly. Visualization will be quite useful here.

Most importantly, since the triangulation / tessaltion being used to define our cells is based upon the notion that each cell is defined as points which are closer that cell's control point than any other cells, we could also calculate cell occupancy by computing the distance of a given ion to each cell control point and assigning it into the cell which yields the minimum distance. Indeed, this will be the general method of indexing used during milestoning analysis.

Therefore, a final and very important check is to ensure that we get identical results by using either our LCOD interval or PCA distance based assignment methods. Any discrepancy in assignments between those two methods would indicate a bug or error that must be addressed.

Once we are satisfied the restarints are working we will need to then create functions that can write out corresponding AMBER restraint files (or corresponding restraint files for whatever simulation engine we are using). Due to large number of half plane restraints that each cell may need, trying to write these by hand would be exceeding cumbersome, tedious, and prone to error, so an automated approach is highly desireable here.

First, lets load our ion and cluster data for testing

### Load Data

In [3]:
dataDir='simulationData'
pcaComponents=np.loadtxt('/'.join([dataDir,'pca_components.cylindricalFilter.txt']))
display(pcaComponents)
pcaCylData=pd.read_csv('/'.join([dataDir,'pca_projection_data.cylindricalFilter.csv']))
clustDat=pd.read_csv('/'.join([dataDir,'cluster_data.cylindricalFilter.csv']))
display(clustDat.head())

clusterCenteroids=pd.read_csv('/'.join([dataDir,'Agglomerative_clustering_centers.csv']))
clustDatGroups=clustDat.groupby('Cluster')

clustVols=[]
for groupName,groupData in clustDatGroups:
    cHull=sp.spatial.ConvexHull(groupData[['X','Y','Z']])
    clustVols.append((groupName,cHull.volume))
    

clustVol=pd.DataFrame(clustVols,columns=['Cluster','Volume'])
display(clustVol.head()) #[clustVol['Cluster'].isin(cTest)])

clusterCenteroids=clusterCenteroids.set_index('Cluster').join(
    clustVol.set_index('Cluster'),rsuffix='').reset_index()
display(clusterCenteroids) #[clusterCenteroids['Cluster'].isin(cTest)])


clusterSummary=clusterCenteroids
tessellationClusters=clusterSummary.index.to_numpy() #[0,1,2,3,4,8,10] 
centeroidColumns=np.concatenate([
    ['Cluster'],
    clusterSummary.columns[3:6],
    clusterSummary.columns[11:]])
tessellationCoordinateColumns=['PCAcyl_2','PCAcyl_3','PCAcyl_1'] #[colName for colName in clusterCenteroids.columns \
                               #if 'PCAcyl' in colName]

tessellationData=clusterCenteroids[
        clusterCenteroids['Cluster'].isin(tessellationClusters)
    ][tessellationCoordinateColumns]
clusterVoronoi=sp.spatial.Voronoi(tessellationData)
clusterDelaunay=sp.spatial.Delaunay(tessellationData)
print('cluster centeroids')
display(clusterCenteroids)
print('cluster vertices')
print(clusterDelaunay.vertices)
print()
print("cluster adjacency")
neiList=defaultdict(set)
for p in clusterDelaunay.vertices:
    for i,j in itertools.combinations(p,2):
        neiList[tessellationClusters[i]].add(tessellationClusters[j])
        neiList[tessellationClusters[j]].add(tessellationClusters[i])

for key in sorted(neiList.keys()):
    print("%d:%s" % (key,','.join([str(i) for i in neiList[key]])))

array([[ 0.40045854,  0.08449305,  0.65258185,  0.46235539,  0.43915636],
       [-0.14434161,  0.90046587, -0.30072427,  0.20338675,  0.19111636],
       [ 0.27838328,  0.07815429, -0.03906275, -0.75636341,  0.58547685],
       [ 0.82572275,  0.19911421, -0.15603285, -0.05535959, -0.50112327],
       [ 0.24389168, -0.3691444 , -0.67663114,  0.41195998,  0.42036715]])

Unnamed: 0  Frame  AtomID AtomType         X         Y         Z  X_Center  \
0           5      1  165552      POT  109.3891   81.3629   25.0487   90.4509   
1           6      1  165554      POT   42.9653   78.8911   51.0144   90.4509   
2           7      1  165557      POT   59.0333   65.9134   93.0642   90.4509   
3           8      1  165570      POT   74.8840  133.9131   21.6081   90.4509   
4           9      1  165581      POT   57.8748  122.7727  107.9835   90.4509   

    Y_Center  Z_Center  ...      D_1178     D_1366     D_2377      D_3796  \
0  136.76246  65.44026  ...  128.234104  47.483162  74.414691   95.227241   
1  136.76246  65.44026  ...  112.140092  72.832906  39.343976  110.823964   
2  136.76246  65.44026  ...   99.317973  92.829412  60.282709  120.622686   
3  136.76246  65.44026  ...  102.972238  24.265077  47.409354   58.214160   
4  136.76246  65.44026  ...   43.343148  84.424088  48.938661   85.049333   

    PCAcyl_0   PCAcyl_1   PCAcyl_2   PCAcyl_3  PCAcyl_4  Cluster  
0   3.949924  58.126858  10.976897 -16.407481  0.257267      130  
1  25.844157  26.064522  55.562696   3.708095 -9.054124       27  
2  51.407127  14.776168  43.409862  -8.833230 -5.342075       99  
3 -34.763068  27.159143  13.749322  17.308974  3.062724      245  
4  19.177857 -41.791883  26.318759  -2.578299  0.682071        1  

[5 rows x 23 columns]

Cluster       Volume
0        0  6031.972613
1        1  2770.546167
2        2  2727.414220
3        3  4566.164794
4        4  3836.497178

Cluster        Frame         AtomID           X           Y           Z  \
0          0  1469.468750  165962.562500   44.682934  166.358437  128.804662   
1          1   928.492063  165651.460317   55.305103  122.662275  111.099722   
2          2  1030.756098  165566.560976  108.445688  191.335907  111.924205   
3          3   883.632653  165721.836735  134.698949  156.352233    8.789557   
4          4  1375.270270  165993.000000   95.947468   99.063916  117.130900   
..       ...          ...            ...         ...         ...         ...   
251      251   706.161290  165756.193548   51.901384  137.112374  106.837881   
252      252   635.434783  165692.608696   19.898983  118.408770   99.818748   
253      253  1792.925926  166071.407407  108.690596  100.968807  115.242111   
254      254  1380.769231  165932.038462   56.438638  126.412912   10.929746   
255      255  1727.666667  165992.518519  116.888822  213.585833   36.811437   

      X_Center    Y_Center   Z_Center          R  ...      D_1178      D_1366  \
0    92.709069  139.608313  62.607678  55.385660  ...   37.869426  118.323749   
1    92.833789  139.335496  62.610575  41.299602  ...   49.906499   91.289160   
2    92.953200  140.221891  62.604540  53.584732  ...   41.556516  103.711981   
3    92.758402  139.430772  62.830846  45.561842  ...  121.596911   52.830699   
4    92.740730  139.467588  62.735740  40.748084  ...   68.521636   92.023583   
..         ...         ...        ...        ...  ...         ...         ...   
251  92.456301  138.832946  63.324074  40.753408  ...   40.099890   88.902974   
252  92.737587  139.159924  62.809383  75.796665  ...   77.713459  104.289743   
253  92.791507  139.777509  62.660913  42.020837  ...   70.709397   90.193080   
254  92.561277  139.216290  62.823223  38.758145  ...  115.214266   45.384938   
255  92.588433  139.407601  62.737716  78.129681  ...  100.368304   87.797644   

         D_2377      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2   PCAcyl_3  \
0     88.049435   98.259369  80.191258 -52.011713  13.472579  14.154026   
1     55.021504   93.321235  33.509643 -36.156256  28.788391  -0.943710   
2    105.311968   60.844022  53.390477 -44.647408 -26.975911  16.142427   
3    100.762198   56.624222  10.474347  45.507644 -26.464210  16.573817   
4     75.995928  100.809818  39.680890 -10.721619  12.570546 -20.549207   
..          ...         ...        ...        ...        ...        ...   
251   53.744565   84.494619  27.744016 -46.607542  24.668731   4.210829   
252   56.176908  112.430294  63.249795 -14.737012  47.705947  13.504091   
253   81.170257   97.813726  36.914376  -6.700063   5.175521 -24.455400   
254   46.942317   80.858865  -2.120087  33.145514  33.121392  21.825892   
255  114.851953   43.497343  47.497608  10.737356 -37.231572  44.130458   

      PCAcyl_4       Volume  
0    10.851485  6031.972613  
1     1.334275  2770.546167  
2     5.201749  2727.414220  
3    -1.188909  4566.164794  
4     0.353862  3836.497178  
..         ...          ...  
251   2.994330   890.325618  
252  -3.139788   554.362935  
253  -0.068655   770.193208  
254  -1.488360  1387.323013  
255  -7.439146   178.154623  

[256 rows x 22 columns]

cluster centeroids


Cluster        Frame         AtomID           X           Y           Z  \
0          0  1469.468750  165962.562500   44.682934  166.358437  128.804662   
1          1   928.492063  165651.460317   55.305103  122.662275  111.099722   
2          2  1030.756098  165566.560976  108.445688  191.335907  111.924205   
3          3   883.632653  165721.836735  134.698949  156.352233    8.789557   
4          4  1375.270270  165993.000000   95.947468   99.063916  117.130900   
..       ...          ...            ...         ...         ...         ...   
251      251   706.161290  165756.193548   51.901384  137.112374  106.837881   
252      252   635.434783  165692.608696   19.898983  118.408770   99.818748   
253      253  1792.925926  166071.407407  108.690596  100.968807  115.242111   
254      254  1380.769231  165932.038462   56.438638  126.412912   10.929746   
255      255  1727.666667  165992.518519  116.888822  213.585833   36.811437   

      X_Center    Y_Center   Z_Center          R  ...      D_1178      D_1366  \
0    92.709069  139.608313  62.607678  55.385660  ...   37.869426  118.323749   
1    92.833789  139.335496  62.610575  41.299602  ...   49.906499   91.289160   
2    92.953200  140.221891  62.604540  53.584732  ...   41.556516  103.711981   
3    92.758402  139.430772  62.830846  45.561842  ...  121.596911   52.830699   
4    92.740730  139.467588  62.735740  40.748084  ...   68.521636   92.023583   
..         ...         ...        ...        ...  ...         ...         ...   
251  92.456301  138.832946  63.324074  40.753408  ...   40.099890   88.902974   
252  92.737587  139.159924  62.809383  75.796665  ...   77.713459  104.289743   
253  92.791507  139.777509  62.660913  42.020837  ...   70.709397   90.193080   
254  92.561277  139.216290  62.823223  38.758145  ...  115.214266   45.384938   
255  92.588433  139.407601  62.737716  78.129681  ...  100.368304   87.797644   

         D_2377      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2   PCAcyl_3  \
0     88.049435   98.259369  80.191258 -52.011713  13.472579  14.154026   
1     55.021504   93.321235  33.509643 -36.156256  28.788391  -0.943710   
2    105.311968   60.844022  53.390477 -44.647408 -26.975911  16.142427   
3    100.762198   56.624222  10.474347  45.507644 -26.464210  16.573817   
4     75.995928  100.809818  39.680890 -10.721619  12.570546 -20.549207   
..          ...         ...        ...        ...        ...        ...   
251   53.744565   84.494619  27.744016 -46.607542  24.668731   4.210829   
252   56.176908  112.430294  63.249795 -14.737012  47.705947  13.504091   
253   81.170257   97.813726  36.914376  -6.700063   5.175521 -24.455400   
254   46.942317   80.858865  -2.120087  33.145514  33.121392  21.825892   
255  114.851953   43.497343  47.497608  10.737356 -37.231572  44.130458   

      PCAcyl_4       Volume  
0    10.851485  6031.972613  
1     1.334275  2770.546167  
2     5.201749  2727.414220  
3    -1.188909  4566.164794  
4     0.353862  3836.497178  
..         ...          ...  
251   2.994330   890.325618  
252  -3.139788   554.362935  
253  -0.068655   770.193208  
254  -1.488360  1387.323013  
255  -7.439146   178.154623  

[256 rows x 22 columns]

cluster vertices
[[  5 173 138  89]
 [228   5 173 138]
 [162 252 147 113]
 ...
 [230  22  54 144]
 [230 177   6 151]
 [230 177 144 151]]

cluster adjacency
0:32,96,34,167,199,43,237,110,239,121,61,62,127
1:33,69,7,72,233,235,115,85,247,185,251,93,31
2:224,167,40,9,11,109,60,239,92,142,148,188
3:164,136,234,45,46,78,17,23,125,95
4:67,135,202,14,47,16,240,81,83,180,182,186,28,253,191
5:228,138,204,173,17,23,216,89,30,255
6:230,7,231,199,137,235,236,109,237,47,177,114,213,151,59,190
7:1,6,137,151,31,32,34,185,59,61,197,199,233,235,110,247,121,251,127
8:97,162,66,196,198,38,241,50,119,254
9:224,2,165,197,40,137,236,60,142,207,51,155,92,190,127
10:99,100,227,70,105,170,28,240,241,16,83,19,181,249,220,254
11:96,2,40,73,239,92,210,148,188,62,255
12:64,134,231,106,108,140,143,207,179,117,214,215,25,155,189
13:37,166,135,76,204,206,111,176,81,212,55,87,63,126,159
14:67,4,101,154,104,235,47,16,83,180,150,182,151,186,28
15:193,100,70,141,240,145,244,245,217,220,63,126,223
16:194,227,100,101,4,135

# Compute Restraint Information

Recall above:

Our $\kappa_{ijd}$ coefficients are then readily visibile as the terms being summed by the left hand side of the inequallity shown in the last line of equation <b>(4)</b> after swapping the positions of the PCA and distance coordinate summations:

<font size=4>
$$
\begin{align}
    LCOD_{ij} & = \sum\limits_{D \in Distances}{(\sum\limits_{k \in PCAmodes} \alpha_{kD}(R_{ik} - c_{ijk})r_{D}) } \nonumber \\
    & = \sum\limits_{D \in Distances}{\kappa_{ijd}r_D};  \nonumber \\
    where & : \kappa_{ijD} = \sum\limits_{k \in PCAmodes}{\alpha_{kD} (R_{ik} - c_{ijk})} \tag{7}
\end{align}
$$
</font>

and the flat bottom region interval for this LCOD restraint, $LCOD_{ij}$ used to restrain our ion to be closer to cell $i$ than cell $j$ is given as:

<font size=4>
\begin{align}
    LCOD_{ij} > \sum\limits_{k \in PCAmodes}{(c_{ijk} R_{iK} - c_{ijk}^2 + (R_{ik} - c_{ijk})(\sum\limits_{D \in Distances}{ \alpha_{kD}\hat{\lambda_D}}) )} \tag{8} \\
\end{align}
</font>

we are now ready to define functions to compute kappa and interval bounds for our restraints and test them on our ion data

### Define LCOD restraint and interval construction functions

In [20]:
def compute_kappa_ijVec(center_i,center_j,PCA_components):
    cij=(center_i+center_j)/2.
    vij=1.*(center_i-cij) # vij = (Ri - cij)
    return(np.array([np.sum(PCA_components[:,D_index]*vij) \
            for D_index in np.arange(PCA_components.shape[1])]))
    
def compute_restraintBound_ij(center_i,center_j,PCA_components,coordinate_means):
    cij=(center_i+center_j)/2.
    vij=1.*(center_i-cij)
    dSum=np.sum([coordinate_means * component for component in PCA_components],axis=1) #summing alpha*lambdaHat over D
    return(np.sum(cij*center_i - cij**2 + vij*dSum))

def compute_kappaMatrix_i(center_i,neighbor_centers,PCA_components):
    return(np.array([compute_kappa_ijVec(center_i,center_j,PCA_components) \
            for center_j in neighbor_centers]))

def compute_restraintBoundArray_i(center_i,neighbor_centers,PCA_components,coordinate_means):
    return(np.array([compute_restraintBound_ij(center_i,center_j,PCA_components,coordinate_means) \
                     for center_j in neighbor_centers]))

### Test restraint construction functions
Lets test these construction functions using the 5 cluster subset we located previously

array([[63.90341628, 78.06315127, 60.4284268 , 68.05441783, 67.62657728]])

In [22]:
cTest=[202,135,211,186,63]

pcaColumns=['PCAcyl_2','PCAcyl_3','PCAcyl_1']
pcaInds=[2,3,1]
distColumns=[colName for colName in clusterCenteroids \
             if 'D_' in colName]
dist_means=clustDat[distColumns].agg('mean').to_frame().T[distColumns].to_numpy().flatten()
display('pca distance means:',dist_means)

print(compute_kappa_ijVec(
                  clusterCenteroids.query('Cluster == 135')[pcaColumns].to_numpy(),
                  clusterCenteroids.query('Cluster == 63')[pcaColumns].to_numpy(),
                  pcaComponents[pcaInds]))
print(compute_restraintBound_ij(
                  clusterCenteroids.query('Cluster == 135')[pcaColumns].to_numpy(),
                  clusterCenteroids.query('Cluster == 63')[pcaColumns].to_numpy(),
                  pcaComponents[pcaInds],
                  dist_means))

ci=135
cj_list=list(neiList[ci])
print(compute_kappaMatrix_i(
    clusterCenteroids.query('Cluster == %s'%ci)[pcaColumns].to_numpy(),
    clusterCenteroids.query('Cluster in %s'%cj_list)[pcaColumns].to_numpy(),
    pcaComponents[pcaInds]))
print(compute_restraintBoundArray_i(
    clusterCenteroids.query('Cluster == %s'%ci)[pcaColumns].to_numpy(),
    clusterCenteroids.query('Cluster in %s'%cj_list)[pcaColumns].to_numpy(),
    pcaComponents[pcaInds],
    dist_means))

'pca distance means:'

array([63.90341628, 78.06315127, 60.4284268 , 68.05441783, 67.62657728])

[ 1.03825516 -6.74152917  2.25626825 -1.53502757 -1.38637915]
-528.3274483306336
[[  4.93612673   3.05883282  -1.6988086    4.76398185  -7.58091081]
 [  8.7490963   -3.82728277   0.51180759  -5.34284141  -2.37723144]
 [  1.20730492  -1.0563638    0.03474756   8.5527949   -9.9539184 ]
 [  1.03825516  -6.74152917   2.25626825  -1.53502757  -1.38637915]
 [  6.20930017  -1.51688157   0.05458457  -8.3029378    3.29013984]
 [  6.82134839   2.95482329  -1.73170858  -0.89505203  -3.27312914]
 [ -9.90361625  -9.86392392   4.44661823   1.09528261   3.16795704]
 [ -2.78277931 -10.01643911   3.7272164    1.48417619  -2.63647194]
 [ -5.33676961  -9.82231743   3.92839373   1.71158184  -0.88325044]
 [ -2.04139528   3.6921213   -1.12450571   2.82265966  -0.14961485]
 [ -7.79650554  -8.42692062   3.69075992   2.50339773   0.61074154]
 [  1.44190277   3.62662382  -1.3887897   -0.84569741   0.94149821]
 [ -2.08309594   6.46828704  -2.02248972   0.3733385    3.26738581]
 [  7.90448241  -3.5396322    0.428

In [26]:
def check_occupancy(rD,kappaMatrix,upperBounds,verbose=False):
    LCODvec=np.array(np.matrix(kappaMatrix)*(np.matrix(rD).T)).flatten()
    if verbose:
        print('rD:',rD)
        print('LCODvec:',LCODvec)
        print('bounds:',upperBounds)
        print('bound checks:',LCODvec>=upperBounds)
    return(np.product(LCODvec >= upperBounds))

In [27]:
ci=135
cj_list=list(neiList[ci])

distColumns=[colName for colName in clusterCenteroids \
             if 'D_' in colName]
dist_means=clustDat[distColumns].agg('mean').to_frame().T[distColumns].to_numpy().flatten()
display('pca distance means:',dist_means)


kappaMat=compute_kappaMatrix_i(
    clusterCenteroids.query('Cluster == %s'%ci)[pcaColumns].to_numpy(),
    clusterCenteroids.query('Cluster in %s'%cj_list)[pcaColumns].to_numpy(),
    pcaComponents[pcaInds])
iBounds=compute_restraintBoundArray_i(
    clusterCenteroids.query('Cluster == %s'%ci)[pcaColumns].to_numpy(),
    clusterCenteroids.query('Cluster in %s'%cj_list)[pcaColumns].to_numpy(),
    pcaComponents[pcaInds],
    dist_means)

coordA=clustDat.query('Cluster == %g'%ci)[distColumns].head(n=1).to_numpy()
coordB=clustDat.query('Cluster == %g'%cj_list[0])[distColumns].head(n=1).to_numpy()

print(check_occupancy(coordA,kappaMat,iBounds,verbose=True))
print(check_occupancy(coordB,kappaMat,iBounds,verbose=True))

'pca distance means:'

array([63.90341628, 78.06315127, 60.4284268 , 68.05441783, 67.62657728])

rD: [[40.31720121 65.88678606 30.9950432  42.44454699 43.06012535]]
LCODvec: [ 223.66291395 -212.70315355  -85.44572749 -457.23622554  -58.6495956
  237.09567408 -728.46380822 -707.15124676 -705.94936633  239.46863534
 -622.60654543  258.68026255  436.04311614 -203.40622418  401.80669701
 -492.36840308 -278.15142632  165.9433543 ]
bounds: [ 103.30810788 -345.5498614  -277.67061728 -528.32744833 -174.03048967
  171.32757623 -974.34929694 -863.87481183 -873.71088566  218.56918875
 -794.3477688   249.37967126  392.1033897  -318.03852373  333.0375021
 -596.02420649 -439.74761013   46.74056115]
bound checks: [ True  True  True  True  True  True  True  True  True  True  True  True
  True  True  True  True  True  True]
1
rD: [[54.52214442 84.01823264 18.1767028  38.53339065 48.76295751]]
LCODvec: [  309.15194477  -157.0376982   -178.11168344  -595.54571528
    52.58742316   394.59997367 -1091.20708465  -996.90993012
 -1021.93748055   279.935437    -939.76536536   371.39718568
   566.83038696 

### Test on cluster 135
Lets check to see how well the occupancy function can correctly assign points into cluster 135
i.e. we want to know when it puts a point from another cluster into cluster 135 (false positives) 
and what points in cluster 135 it fails to correctly assign to cluster 135 (false negatives).

In [28]:
tqdm.tqdm.pandas(tqdm.tqdm_notebook)

C:\ProgramData\Anaconda3\lib\site-packages\tqdm\std.py:658: FutureWarning:

The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version



In [48]:
ci=135
cj_list=list(neiList[ci])

distColumns=[colName for colName in clusterCenteroids \
             if 'D_' in colName]
dist_means=clustDat[distColumns].agg('mean').to_frame().T[distColumns].to_numpy().flatten()
display('pca distance means:',dist_means)


kappaMat=compute_kappaMatrix_i(
    clusterCenteroids.query('Cluster == %s'%ci)[pcaColumns].to_numpy(),
    clusterCenteroids.query('Cluster in %s'%cj_list)[pcaColumns].to_numpy(),
    pcaComponents[pcaInds])
iBounds=compute_restraintBoundArray_i(
    clusterCenteroids.query('Cluster == %s'%ci)[pcaColumns].to_numpy(),
    clusterCenteroids.query('Cluster in %s'%cj_list)[pcaColumns].to_numpy(),
    pcaComponents[pcaInds],
    dist_means)

checkDat=clustDat.copy()
checkDat['occupancy_135']=checkDat[distColumns].progress_apply(
        lambda x: check_occupancy(x.to_numpy(),kappaMat,iBounds),
        axis=1
    )
checkDat['Check_135']=checkDat[['Cluster','occupancy_135']].apply(
    lambda x: (x[0]==135)==x[1],axis=1)
checkDat.query('Check_135 == False').groupby('Cluster').count()

'pca distance means:'

array([63.90341628, 78.06315127, 60.4284268 , 68.05441783, 67.62657728])





  0%|          | 0/17109 [00:00<?, ?it/s]



 13%|█▎        | 2238/17109 [00:00<00:00, 22217.19it/s]



 29%|██▉       | 4972/17109 [00:00<00:00, 23496.15it/s]



 46%|████▌     | 7875/17109 [00:00<00:00, 24874.55it/s]



 62%|██████▏   | 10610/17109 [00:00<00:00, 25516.53it/s]



 78%|███████▊  | 13425/17109 [00:00<00:00, 26199.78it/s]



100%|██████████| 17109/17109 [00:00<00:00, 26762.42it/s]


Unnamed: 0  Frame  AtomID  AtomType   X   Y   Z  X_Center  Y_Center  \
Cluster                                                                        
63                6      6       6         6   6   6   6         6         6   
135              12     12      12        12  12  12  12        12        12   
186               8      8       8         8   8   8   8         8         8   
202               6      6       6         6   6   6   6         6         6   

         Z_Center  ...  D_1366  D_2377  D_3796  PCAcyl_0  PCAcyl_1  PCAcyl_2  \
Cluster            ...                                                         
63              6  ...       6       6       6         6         6         6   
135            12  ...      12      12      12        12        12        12   
186             8  ...       8       8       8         8         8         8   
202             6  ...       6       6       6         6         6         6   

         PCAcyl_3  PCAcyl_4  occupancy_135  Check_135  
Cluster                                                
63              6         6              6          6  
135            12        12             12         12  
186             8         8              8          8  
202             6         6              6          6  

[4 rows x 24 columns]

### Analyze false positive / negative rates
In the cell above we displayed counts of all the incorrectly assigned points by cluster... so for cluster 135,
this is the number of false positives, and for the other clusters, these are false negatives.
Lets get a look at the percentage of false negative / false positives by cluster.

We again note that such discrepancies are expected since we know that our LCOD intervals, which are based upon radial distance measurements, do not map linearly into XYZ cartesian coordinates. Thus, we expect that even though our cells should be convex and exhbit planar boundaries in LCOD / PCA space, the same corresponding projections back to XYZ space will yield cells with curved boundaries. This necessarily means that most cells will be concave on at least one boundary. That also means that some points get assigned to different LCOD cells than XYZ cluster from which that cell was constructed.

In [78]:
display(checkDat.query('Check_135 == False').groupby('Cluster').count()['Check_135'])
display(100* checkDat.query('Check_135 == False').groupby('Cluster').count()['Check_135'] / \
        checkDat.groupby('Cluster').count().iloc[[63,135,186,202]]['Check_135'])

Cluster
63      6
135    12
186     8
202     6
Name: Check_135, dtype: int64

Cluster
63     5.940594
135    7.547170
186    5.031447
202    5.000000
Name: Check_135, dtype: float64

### Cross Check PCA-Distance Assignment vs LCOD-Interval Assignment
As we mentioned earlier, our LCOD interval based definition of cell assignment should match exactly with assignment based on distance (in PCA space) to the nearest cell center.

Under our LCOD method, cell assignment must be performed over each cell individually. To that end, we first construct a dictionary of LCOD cells.

### Construct LCOD interval dictionary

In [85]:
pcaColumns=['PCAcyl_2','PCAcyl_3','PCAcyl_1']
pcaInds=[2,3,1]
componentData=pcaComponents[pcaInds]

distColumns=[colName for colName in clusterCenteroids \
             if 'D_' in colName]
dist_means=clustDat[distColumns].agg('mean').to_frame().T[distColumns].to_numpy().flatten()

lcod_dict={}
for iCluster in tqdm.tqdm_notebook(clusterCenteroids.Cluster.unique(),desc="LCOD Generation"):
    iCluster_center=clusterCenteroids.query('Cluster == %g'%iCluster)[pcaColumns].to_numpy()
    jCluster_list=list(neiList[iCluster])
    jCluster_centers=clusterCenteroids.query('Cluster in %s'%jCluster_list)[pcaColumns].to_numpy()
    lcod_dict[iCluster]=(compute_kappaMatrix_i(iCluster_center,jCluster_centers,componentData),
                         compute_restraintBoundArray_i(iCluster_center,jCluster_centers,componentData,dist_means))
print("lcod interval data for cell %g:"%list(lcod_dict.keys())[0],
      lcod_dict[list(lcod_dict.keys())[0]])

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: TqdmDeprecationWarning:

This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`




lcod interval data for cell 0: (array([[ 3.57799009e+00,  1.12372282e+00, -7.84844376e-01,
         5.46178591e-01, -2.88766590e+00],
       [ 2.78894692e+00, -8.55173466e-01,  1.52186840e-02,
        -7.78373759e-01, -1.58177719e+00],
       [-2.95690175e+00, -3.75631217e+00,  1.70251949e+00,
        -3.68333656e+00,  4.76704013e+00],
       [ 1.71392467e-01, -6.47600212e-01,  1.57888550e-01,
         2.02777713e+00, -2.40121022e+00],
       [-3.76830543e+00, -4.22624348e+00,  1.94927532e+00,
        -3.56852326e+00,  5.10980309e+00],
       [-1.74792206e+00, -2.13810142e+00,  1.08086064e+00,
        -6.55275234e+00,  7.29802779e+00],
       [-2.52882956e+00, -3.38106717e+00,  1.43601252e+00,
         1.79233367e-01,  6.33903688e-01],
       [ 1.85388080e+00, -5.11764023e+00,  1.65948902e+00,
        -3.75389372e+00,  7.80321644e-01],
       [ 3.89624006e+00,  2.53249184e-01, -3.76175315e-01,
        -5.47858584e+00,  2.72535843e+00],
       [ 3.86195826e+00,  7.43914775e+00, -2.8721

### Define LCOD based cell assignment
Using our dictionary of LCOD cells, we can now check for cell occupancy of any ion against all defined cells. We can then count how many cells the ion 'occupies'. If this value is anything except a 1, then we have a problem.

In [88]:
def count_lcod_occupancy(rD,LCOD_dict):
    return(np.sum([
        check_occupancy(rD,LCOD_dict[keyVal][0],LCOD_dict[keyVal][1]) \
        for keyVal in LCOD_dict
    ]))

In [93]:
clustDat['LCOD_Count']=clustDat[distColumns].apply(
    lambda x: count_lcod_occupancy(x,lcod_dict),axis=1)
clustDat.query('LCOD_Count != 1')







 15%|█▌        | 2599/17109 [00:40<02:25, 99.50it/s]

Empty DataFrame
Columns: [Unnamed: 0, Frame, AtomID, AtomType, X, Y, Z, X_Center, Y_Center, Z_Center, R, Theta, D_958, D_1178, D_1366, D_2377, D_3796, PCAcyl_0, PCAcyl_1, PCAcyl_2, PCAcyl_3, PCAcyl_4, Cluster, LCOD_Count]
Index: []

[0 rows x 24 columns]

### Assign ions to cells using LCOD intervals

In [103]:
def assign_lcod_cell(rD,LCOD_dict):
    cellArr=np.array([keyVal for keyVal in LCOD_dict])
    return(cellArr[np.nonzero([
        check_occupancy(rD,LCOD_dict[keyVal][0],LCOD_dict[keyVal][1]) \
        for keyVal in LCOD_dict
    ])][0])

In [104]:
clustDat['LCOD_Cell']=clustDat[distColumns].apply(
    lambda x: assign_lcod_cell(x,lcod_dict),axis=1)
clustDat.head()

Unnamed: 0  Frame  AtomID AtomType         X         Y         Z  X_Center  \
0           5      1  165552      POT  109.3891   81.3629   25.0487   90.4509   
1           6      1  165554      POT   42.9653   78.8911   51.0144   90.4509   
2           7      1  165557      POT   59.0333   65.9134   93.0642   90.4509   
3           8      1  165570      POT   74.8840  133.9131   21.6081   90.4509   
4           9      1  165581      POT   57.8748  122.7727  107.9835   90.4509   

    Y_Center  Z_Center  ...     D_2377      D_3796   PCAcyl_0   PCAcyl_1  \
0  136.76246  65.44026  ...  74.414691   95.227241   3.949924  58.126858   
1  136.76246  65.44026  ...  39.343976  110.823964  25.844157  26.064522   
2  136.76246  65.44026  ...  60.282709  120.622686  51.407127  14.776168   
3  136.76246  65.44026  ...  47.409354   58.214160 -34.763068  27.159143   
4  136.76246  65.44026  ...  48.938661   85.049333  19.177857 -41.791883   

    PCAcyl_2   PCAcyl_3  PCAcyl_4  Cluster  LCOD_Count  LCOD_Cell  
0  10.976897 -16.407481  0.257267      130           1        130  
1  55.562696   3.708095 -9.054124       27           1         27  
2  43.409862  -8.833230 -5.342075       99           1        181  
3  13.749322  17.308974  3.062724      245           1        245  
4  26.318759  -2.578299  0.682071        1           1          1  

[5 rows x 25 columns]

In [115]:
def assign_PCAdist_cell(rk,centeroids_PCA,centeroid_labels):
    return(centeroid_labels[
        np.argmin(np.sum(
            (np.atleast_2d(centeroids_PCA)-np.atleast_2d(rk))**2,
            axis=1
        ))])

In [118]:
centeroidDistances=clusterCenteroids[pcaColumns].to_numpy()
centeroidClusters=clusterCenteroids['Cluster'].to_numpy()
clustDat['PCAdist_Cell']=clustDat[pcaColumns].apply(
    lambda x: assign_PCAdist_cell(x,centeroidDistances,centeroidClusters),
    axis=1)
display(clustDat.head())
display(clustDat.query('LCOD_Cell != PCAdist_Cell'))

Unnamed: 0  Frame  AtomID AtomType         X         Y         Z  X_Center  \
0           5      1  165552      POT  109.3891   81.3629   25.0487   90.4509   
1           6      1  165554      POT   42.9653   78.8911   51.0144   90.4509   
2           7      1  165557      POT   59.0333   65.9134   93.0642   90.4509   
3           8      1  165570      POT   74.8840  133.9131   21.6081   90.4509   
4           9      1  165581      POT   57.8748  122.7727  107.9835   90.4509   

    Y_Center  Z_Center  ...      D_3796   PCAcyl_0   PCAcyl_1   PCAcyl_2  \
0  136.76246  65.44026  ...   95.227241   3.949924  58.126858  10.976897   
1  136.76246  65.44026  ...  110.823964  25.844157  26.064522  55.562696   
2  136.76246  65.44026  ...  120.622686  51.407127  14.776168  43.409862   
3  136.76246  65.44026  ...   58.214160 -34.763068  27.159143  13.749322   
4  136.76246  65.44026  ...   85.049333  19.177857 -41.791883  26.318759   

    PCAcyl_3  PCAcyl_4  Cluster  LCOD_Count  LCOD_Cell  PCAdist_Cell  
0 -16.407481  0.257267      130           1        130           130  
1   3.708095 -9.054124       27           1         27            27  
2  -8.833230 -5.342075       99           1        181           181  
3  17.308974  3.062724      245           1        245           245  
4  -2.578299  0.682071        1           1          1             1  

[5 rows x 26 columns]

Empty DataFrame
Columns: [Unnamed: 0, Frame, AtomID, AtomType, X, Y, Z, X_Center, Y_Center, Z_Center, R, Theta, D_958, D_1178, D_1366, D_2377, D_3796, PCAcyl_0, PCAcyl_1, PCAcyl_2, PCAcyl_3, PCAcyl_4, Cluster, LCOD_Count, LCOD_Cell, PCAdist_Cell]
Index: []

[0 rows x 26 columns]

### Highlight differences between LCOD interval cells vs XYZ clusters

Now that we have assigned each ion to a cell using LCOD (and verified that it is faithfully reproducing assignment based
upon a voronoi tesselation created from the PCA space cluster centers). We can visualize which ions are getting put into
different LCOD cells than the corresponding XYZ cluster